In [2]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait, Select
from selenium.webdriver.support import expected_conditions as EC
import pandas as pd
import time, os

# ─── CONFIG ─────────────────────────────────────────────────────────────
URL               = "https://assamtenders.gov.in/nicgep/app?page=WebTenderStatusLists&service=page"
DEPARTMENT_VALUE  = "108"   # ← set this to the Assam-specific value
DEPARTMENT_NAME   = " Public Works Roads Department  "      # will be populated at runtime
FROM_DATE         = "01/07/2024"
TO_DATE           = "15/07/2025"
OUTPUT_XLS        = "Public Works Roads Department Assam .xlsx"

# ─── BROWSER SETUP ──────────────────────────────────────────────────────
driver = webdriver.Chrome()
driver.maximize_window()
driver.get(URL)
time.sleep(2)

# ─── PICK DEPARTMENT ────────────────────────────────────────────────────
select = Select(driver.find_element(By.ID, "OrganName"))
select.select_by_value(DEPARTMENT_VALUE)
DEPARTMENT_NAME = select.first_selected_option.text.strip()
print(f"🔎 Using Department: {DEPARTMENT_NAME}")

# ─── SET DATE FILTERS ───────────────────────────────────────────────────
for fld_id, val in [("publishedFromDate", FROM_DATE), ("publishedToDate", TO_DATE)]:
    el = driver.find_element(By.ID, fld_id)
    driver.execute_script("arguments[0].removeAttribute('readonly')", el)
    el.clear()
    el.send_keys(val)

# ─── CAPTCHA ───────────────────────────────────────────────────────────
png = "captcha_assam.png"
with open(png, "wb") as f:
    f.write(driver.find_element(By.ID, "captchaImage").screenshot_as_png)
print(f"✔ CAPTCHA saved to {png}. Please open it to read.")
captcha = input("Enter CAPTCHA: ")
driver.find_element(By.ID, "captchaText").send_keys(captcha)
driver.find_element(By.ID, "Search").click()
WebDriverWait(driver, 20).until(EC.presence_of_element_located((By.ID, "tabList")))

# ─── FIELD EXTRACTOR ────────────────────────────────────────────────────
def get_field_value(label):
    target = label.strip().lower()
    captions = driver.find_elements(By.XPATH, "//td[contains(@class,'caption')]")
    for cap in captions:
        if target in cap.text.strip().lower():
            try:
                return cap.find_element(By.XPATH, "following-sibling::td[1]").text.strip()
            except:
                return ""
    return ""

# ─── SCRAPE & PAGINATE ──────────────────────────────────────────────────
all_data = []

while True:
    rows = driver.find_elements(By.XPATH, "//table[@id='tabList']//tr[@class='even' or @class='odd']")
    for idx in range(len(rows)):
        try:
            # refresh row list each iteration
            rows = driver.find_elements(By.XPATH, "//table[@id='tabList']//tr[@class='even' or @class='odd']")
            row = rows[idx]
            cells = row.find_elements(By.TAG_NAME, "td")
            if len(cells) < 6:
                continue

            sno, tid, title, orgs, stage, status = [c.text.strip() for c in cells[:6]]

            # open detail popup
            row.find_element(By.XPATH, ".//td[last()]/a").click()
            WebDriverWait(driver, 10).until(EC.element_to_be_clickable((By.ID, "DirectLink"))).click()
            WebDriverWait(driver, 10).until(lambda d: len(d.window_handles) > 1)
            driver.switch_to.window(driver.window_handles[-1])
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.TAG_NAME, "table")))

            # extract fields
            record = {
                "Department":               DEPARTMENT_NAME,
                "S.No":                     sno.rstrip('.'),
                "Tender ID":                tid,
                "Title & Ref No.":          title,
                "Organisation Chain":       orgs,
                "Tender Stage":             stage,
                "Status":                   status,
                "Publish Date":             get_field_value("Publish Date"),
                "Bid Submission End":       get_field_value("Bid Submission End Date"),
                "Tender Value (₹)":         get_field_value("Tender Value"),
                "Location":                 get_field_value("Location"),
                "Pincode":                  get_field_value("Pincode"),
                "Period Of Work (Days)":    get_field_value("Period Of Work"),
                "Address":                  get_field_value("Address"),
            }
            all_data.append(record)
            print(f"✔ Row {sno}: {tid} extracted")

            # close detail and return to list
            driver.close()
            driver.switch_to.window(driver.window_handles[0])
            WebDriverWait(driver, 10).until(
                EC.element_to_be_clickable((By.XPATH, "//a[contains(text(),'Back')]"))
            ).click()
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.ID, "tabList")))

        except Exception as e:
            print(f"❌ Row {idx+1} error: {e}")
            driver.switch_to.window(driver.window_handles[0])
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.ID, "tabList")))

    # move to next page, if any
    try:
        driver.find_element(By.ID, "loadNext").click()
        WebDriverWait(driver, 20).until(EC.presence_of_element_located((By.ID, "tabList")))
    except:
        break

# ─── EXPORT TO EXCEL ───────────────────────────────────────────────────
df = pd.DataFrame(all_data)
df.to_excel(OUTPUT_XLS, index=False)
print(f"\n✅ Done! Saved {len(all_data)} records to {OUTPUT_XLS}")

driver.quit()


🔎 Using Department: Public Works Building and NH Department
✔ CAPTCHA saved to captcha_assam.png. Please open it to read.


Enter CAPTCHA:  78JNLV


✔ Row 1.: 2025_PWBNH_45590_1 extracted
✔ Row 2.: 2025_PWBNH_45568_1 extracted
✔ Row 3.: 2025_PWBNH_45564_1 extracted
✔ Row 4.: 2025_PWBNH_45551_1 extracted
✔ Row 5.: 2025_PWBNH_45550_1 extracted
✔ Row 6.: 2025_PWBNH_45536_1 extracted
✔ Row 7.: 2025_PWBNH_45493_1 extracted
✔ Row 8.: 2025_PWBNH_45486_1 extracted
✔ Row 9.: 2025_PWBNH_45421_1 extracted
✔ Row 10.: 2025_PWBNH_45417_1 extracted
✔ Row 11.: 2025_PWBNH_45407_1 extracted
✔ Row 12.: 2025_PWBNH_45402_1 extracted
✔ Row 13.: 2025_PWBNH_45396_1 extracted
✔ Row 14.: 2025_PWBNH_45394_1 extracted
✔ Row 15.: 2025_PWBNH_45388_1 extracted
✔ Row 16.: 2025_PWBNH_45384_1 extracted
✔ Row 17.: 2025_PWBNH_45380_1 extracted
✔ Row 18.: 2025_PWBNH_45377_1 extracted
✔ Row 19.: 2025_PWBNH_45351_1 extracted
✔ Row 20.: 2025_PWBNH_45324_1 extracted
✔ Row 21.: 2025_PWBNH_45298_1 extracted
✔ Row 22.: 2025_PWBNH_45297_1 extracted
✔ Row 23.: 2025_PWBNH_45288_1 extracted
✔ Row 24.: 2025_PWBNH_45281_1 extracted
✔ Row 25.: 2025_PWBNH_45280_1 extracted
✔ Row 26.

In [ ]:
##MP-PASTDATA SCRAPE##

In [2]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait, Select
from selenium.webdriver.support import expected_conditions as EC
import pandas as pd
import time, os

# ─── CONFIG ─────────────────────────────────────────────────────────────
URL               = "https://mptenders.gov.in/nicgep/app?page=WebTenderStatusLists&service=page"
DEPARTMENT_VALUE  = "143"   # ← set this to the Assam-specific value
DEPARTMENT_NAME   = "Madhya Pradesh Rural Road Development Authority"      # will be populated at runtime
FROM_DATE         = "02/06/2025"
TO_DATE           = "30/06/2025"
OUTPUT_XLS        = "MP_PAST_Madhya Pradesh Rural Road Development Authority1.xlsx"

# ─── BROWSER SETUP ──────────────────────────────────────────────────────
driver = webdriver.Chrome()
driver.maximize_window()
driver.get(URL)
time.sleep(2)

# ─── PICK DEPARTMENT ────────────────────────────────────────────────────
select = Select(driver.find_element(By.ID, "OrganName"))
select.select_by_value(DEPARTMENT_VALUE)
DEPARTMENT_NAME = select.first_selected_option.text.strip()
print(f"🔎 Using Department: {DEPARTMENT_NAME}")

# ─── SET DATE FILTERS ───────────────────────────────────────────────────
for fld_id, val in [("publishedFromDate", FROM_DATE), ("publishedToDate", TO_DATE)]:
    el = driver.find_element(By.ID, fld_id)
    driver.execute_script("arguments[0].removeAttribute('readonly')", el)
    el.clear()
    el.send_keys(val)

# ─── CAPTCHA ───────────────────────────────────────────────────────────
png = "captcha_assam.png"
with open(png, "wb") as f:
    f.write(driver.find_element(By.ID, "captchaImage").screenshot_as_png)
print(f"✔ CAPTCHA saved to {png}. Please open it to read.")
captcha = input("Enter CAPTCHA: ")
driver.find_element(By.ID, "captchaText").send_keys(captcha)
driver.find_element(By.ID, "Search").click()
WebDriverWait(driver, 20).until(EC.presence_of_element_located((By.ID, "tabList")))

# ─── FIELD EXTRACTOR ────────────────────────────────────────────────────
def get_field_value(label):
    target = label.strip().lower()
    captions = driver.find_elements(By.XPATH, "//td[contains(@class,'caption')]")
    for cap in captions:
        if target in cap.text.strip().lower():
            try:
                return cap.find_element(By.XPATH, "following-sibling::td[1]").text.strip()
            except:
                return ""
    return ""

# ─── SCRAPE & PAGINATE ──────────────────────────────────────────────────
all_data = []

while True:
    rows = driver.find_elements(By.XPATH, "//table[@id='tabList']//tr[@class='even' or @class='odd']")
    for idx in range(len(rows)):
        try:
            # refresh row list each iteration
            rows = driver.find_elements(By.XPATH, "//table[@id='tabList']//tr[@class='even' or @class='odd']")
            row = rows[idx]
            cells = row.find_elements(By.TAG_NAME, "td")
            if len(cells) < 6:
                continue

            sno, tid, title, orgs, stage, status = [c.text.strip() for c in cells[:6]]

            # open detail popup
            row.find_element(By.XPATH, ".//td[last()]/a").click()
            WebDriverWait(driver, 10).until(EC.element_to_be_clickable((By.ID, "DirectLink"))).click()
            WebDriverWait(driver, 10).until(lambda d: len(d.window_handles) > 1)
            driver.switch_to.window(driver.window_handles[-1])
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.TAG_NAME, "table")))

            # extract fields
            record = {
                "Department":               DEPARTMENT_NAME,
                "S.No":                     sno.rstrip('.'),
                "Tender ID":                tid,
                "Title & Ref No.":          title,
                "Organisation Chain":       orgs,
                "Tender Stage":             stage,
                "Status":                   status,
                "Publish Date":             get_field_value("Publish Date"),
                "Bid Submission End":       get_field_value("Bid Submission End Date"),
                "Tender Value (₹)":         get_field_value("Tender Value"),
                "Location":                 get_field_value("Location"),
                "Pincode":                  get_field_value("Pincode"),
                "Period Of Work (Days)":    get_field_value("Period Of Work"),
                "Address":                  get_field_value("Address"),
            }
            all_data.append(record)
            print(f"✔ Row {sno}: {tid} extracted")

            # close detail and return to list
            driver.close()
            driver.switch_to.window(driver.window_handles[0])
            WebDriverWait(driver, 10).until(
                EC.element_to_be_clickable((By.XPATH, "//a[contains(text(),'Back')]"))
            ).click()
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.ID, "tabList")))

        except Exception as e:
            print(f"❌ Row {idx+1} error: {e}")
            driver.switch_to.window(driver.window_handles[0])
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.ID, "tabList")))

    # move to next page, if any
    try:
        driver.find_element(By.ID, "loadNext").click()
        WebDriverWait(driver, 20).until(EC.presence_of_element_located((By.ID, "tabList")))
    except:
        break

# ─── EXPORT TO EXCEL ───────────────────────────────────────────────────
df = pd.DataFrame(all_data)
df.to_excel(OUTPUT_XLS, index=False)
print(f"\n✅ Done! Saved {len(all_data)} records to {OUTPUT_XLS}")

driver.quit()


🔎 Using Department: Madhya Pradesh Rural Road Development Authority
✔ CAPTCHA saved to captcha_assam.png. Please open it to read.


Enter CAPTCHA:  A534AD


✔ Row 1.: 2025_MPRRD_433681_1 extracted
✔ Row 2.: 2025_MPRRD_430820_6 extracted
✔ Row 3.: 2025_MPRRD_430820_5 extracted
✔ Row 4.: 2025_MPRRD_430820_4 extracted
✔ Row 5.: 2025_MPRRD_430820_3 extracted
✔ Row 6.: 2025_MPRRD_430820_2 extracted
✔ Row 7.: 2025_MPRRD_430820_1 extracted
✔ Row 8.: 2025_MPRRD_430224_1 extracted
✔ Row 9.: 2025_MPRRD_429526_2 extracted
✔ Row 10.: 2025_MPRRD_429526_1 extracted
✔ Row 11.: 2025_MPRRD_429510_3 extracted
✔ Row 12.: 2025_MPRRD_429510_2 extracted
✔ Row 13.: 2025_MPRRD_429510_1 extracted
✔ Row 14.: 2025_MPRRD_428028_9 extracted
✔ Row 15.: 2025_MPRRD_428028_8 extracted
✔ Row 16.: 2025_MPRRD_428028_7 extracted
✔ Row 17.: 2025_MPRRD_428028_6 extracted
✔ Row 18.: 2025_MPRRD_428028_5 extracted
✔ Row 19.: 2025_MPRRD_428028_40 extracted
✔ Row 20.: 2025_MPRRD_428028_4 extracted
✔ Row 21.: 2025_MPRRD_428028_39 extracted
✔ Row 22.: 2025_MPRRD_428028_38 extracted
✔ Row 23.: 2025_MPRRD_428028_37 extracted
✔ Row 24.: 2025_MPRRD_428028_36 extracted
✔ Row 25.: 2025_MPRR

In [3]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.ui import WebDriverWait, Select
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import TimeoutException, NoSuchElementException, StaleElementReferenceException
from datetime import datetime
import pandas as pd, os, re, shutil, time

# ───────────────── CONFIG ─────────────────
URL = "https://mptenders.gov.in/nicgep/app?page=WebTenderStatusLists&service=page"
DEPTS = [("MP Water and Land Management Institute", "208")]
published_from = "01/06/2024"
published_to = "30/06/2025"

dept_name_clean = DEPTS[0][0].replace(" ", "_")
OUT_XLSX = f"MP_tenders_{dept_name_clean}_{datetime.today().strftime('%d_%m_%Y')}.xlsx"
DL_ROOT = os.path.join(os.getcwd(), "downloads")
os.makedirs(DL_ROOT, exist_ok=True)
_clean = lambda s: re.sub(r"[^\d.]", "", s.strip())

def dept_dir(name: str) -> str:
    p = os.path.join(DL_ROOT, name)
    os.makedirs(p, exist_ok=True)
    return p

def await_download(before, target_dir, timeout=40):
    WebDriverWait(drv, timeout).until(
        lambda _: any(f.endswith((".xls", ".xlsx", ".pdf")) and not f.endswith(".crdownload")
                      for f in set(os.listdir(DL_ROOT)) - before))
    f = next(x for x in os.listdir(DL_ROOT) if x not in before and not x.endswith(".crdownload"))
    shutil.move(os.path.join(DL_ROOT, f), os.path.join(target_dir, f))
    print(f"⬇️  Downloaded file: {f} → {target_dir}")

# ───────────── DRIVER ─────────────
opt = webdriver.ChromeOptions()
opt.add_experimental_option("prefs", {
    "download.default_directory": DL_ROOT,
    "download.prompt_for_download": False,
    "safebrowsing.enabled": True
})
drv = webdriver.Chrome(options=opt)
drv.maximize_window()
print(f"📅  {published_from} → {published_to}")

all_rows = []
try:
    drv.get(URL)
    time.sleep(2)

    open("captcha.png", "wb").write(drv.find_element(By.ID, "captchaImage").screenshot_as_png)
    try:
        os.startfile("captcha.png")
    except FileNotFoundError:
        pass
    drv.find_element(By.ID, "captchaText").send_keys(input("Enter CAPTCHA: "))
    print("✅ CAPTCHA solved.\n")

    main_tab = drv.current_window_handle

    for dept, val in DEPTS:
        print(f"🔍 {dept}")
        Select(drv.find_element(By.ID, "OrganName")).select_by_value(val)

        for box, date in [("publishedFromDate", published_from), ("publishedToDate", published_to)]:
            drv.execute_script("document.getElementById(arguments[0]).removeAttribute('readonly');", box)
            elm = drv.find_element(By.ID, box)
            elm.clear()
            elm.send_keys(date)

        drv.find_element(By.ID, "Search").click()
        WebDriverWait(drv, 30).until(EC.presence_of_element_located((By.ID, "tabList")))

        # ✅ Extract total record count
        try:
            WebDriverWait(drv, 10).until(EC.presence_of_element_located((By.XPATH, "//span[@id='If_41']/b")))
            total_text = drv.find_element(By.XPATH, "//span[@id='If_41']/b").text
            match = re.search(r'Total records:\s*(\d+)', total_text)
            if match:
                print(f"📊 Total tenders listed: {match.group(1)}\n")
        except Exception as e:
            print(f"⚠️ Could not extract total records count: {e}")

        page = 1
        seen_ids = set()

        while True:
            rows = drv.find_elements(By.XPATH, "//table[@id='tabList']//tr[td]")
            current_page_ids = set()

            for row in rows:
                try:
                    tds = row.find_elements(By.TAG_NAME, "td")
                    if len(tds) < 6:
                        continue
                    anchors = tds[5].find_elements(By.TAG_NAME, "a")
                    if not anchors:
                        continue

                    sno, tid = [tds[i].text.strip() for i in (0, 1)]
                    if tid in seen_ids:
                        continue
                    current_page_ids.add(tid)
                    seen_ids.add(tid)

                    link = anchors[0]
                    drv.execute_script("arguments[0].setAttribute('target','_blank');", link)
                    link.send_keys(Keys.CONTROL + Keys.RETURN)
                    WebDriverWait(drv, 8).until(lambda d: len(d.window_handles) > 1)
                    detail_tab = [h for h in drv.window_handles if h != main_tab][-1]
                    drv.switch_to.window(detail_tab)

                    WebDriverWait(drv, 8).until(
                        EC.element_to_be_clickable((By.XPATH, "//a[contains(text(),'View More Details')]"))
                    ).click()

                    remark = "No"
                    save_to = os.path.join(dept_dir(dept), tid)
                    os.makedirs(save_to, exist_ok=True)

                    try:
                        direct = drv.find_elements(
                            By.XPATH,
                            "//a[@id='BOQ' or contains(text(),'BOQ Comparative Chart') or contains(@href,'FrontEndViewBidSummaryDetailsPrint')]")
                        if direct:
                            before = set(os.listdir(DL_ROOT))
                            direct[0].click()
                            await_download(before, save_to)
                            remark = "Yes"
                        else:
                            stage_link = WebDriverWait(drv, 6).until(
                                EC.element_to_be_clickable((By.XPATH, "//a[contains(@onclick,'openPopUp') or starts-with(@id,'DirectLink_')]")))
                            stage_link.send_keys(Keys.CONTROL + Keys.RETURN)
                            WebDriverWait(drv, 6).until(lambda d: len(d.window_handles) > 2)
                            pop = [h for h in drv.window_handles if h not in (main_tab, detail_tab)][0]
                            drv.switch_to.window(pop)
                            chart = WebDriverWait(drv, 8).until(
                                EC.element_to_be_clickable((By.XPATH, "//*[@id='BOQ' or starts-with(@id,'CHART')]")))
                            before = set(os.listdir(DL_ROOT))
                            chart.click()
                            await_download(before, save_to)
                            remark = "Yes"
                    except Exception:
                        pass

                    for h in [h for h in drv.window_handles if h != main_tab]:
                        drv.switch_to.window(h)
                        drv.close()
                    drv.switch_to.window(main_tab)

                    all_rows.append({
                        "Department": dept,
                        "S.No": sno,
                        "Tender ID": tid,
                        "Remark": remark
                    })
                    print(f"   ➕ {tid} ({remark})")

                except (StaleElementReferenceException, NoSuchElementException) as e:
                    print(f"⚠️ Skipping a row due to: {e}")
                    continue
                except Exception as e:
                    print(f"⚠️ Error processing tender: {e}")
                    continue

            print(f"📃 Page {page} | Collected so far: {len(all_rows)}")

            # ✅ Fixed pagination logic using correct ID
            try:
                next_btn = WebDriverWait(drv, 10).until(
                    EC.element_to_be_clickable((By.ID, "loadNext"))
                )
                drv.execute_script("arguments[0].scrollIntoView();", next_btn)
                next_btn.click()
                WebDriverWait(drv, 10).until(EC.staleness_of(rows[0]))
                time.sleep(2)
                page += 1
            except Exception as e:
                print("⛔ No more pages or failed to go next:", e)
                break

finally:
    if all_rows:
        pd.DataFrame(all_rows).to_excel(OUT_XLSX, index=False)
        print(f"\n✅ Rows written: {len(all_rows)} → {OUT_XLSX}")
        print(f"📂 BOQs → {DL_ROOT}/<Department>/<TenderID>/")
    else:
        print("\n⚠️ Script finished but collected ZERO rows — "
              "verify the date filter or that tenders exist.")
    drv.quit()


📅  01/06/2024 → 30/06/2025


Enter CAPTCHA:  uX1K44


✅ CAPTCHA solved.

🔍 MP Water and Land Management Institute
⚠️ Could not extract total records count: Message: 
Stacktrace:
	GetHandleVerifier [0x0x7ff66266e935+77845]
	GetHandleVerifier [0x0x7ff66266e990+77936]
	(No symbol) [0x0x7ff662429cda]
	(No symbol) [0x0x7ff6624806aa]
	(No symbol) [0x0x7ff66248095c]
	(No symbol) [0x0x7ff6624d3d07]
	(No symbol) [0x0x7ff6624a890f]
	(No symbol) [0x0x7ff6624d0b07]
	(No symbol) [0x0x7ff6624a86a3]
	(No symbol) [0x0x7ff662471791]
	(No symbol) [0x0x7ff662472523]
	GetHandleVerifier [0x0x7ff66294684d+3059501]
	GetHandleVerifier [0x0x7ff662940c0d+3035885]
	GetHandleVerifier [0x0x7ff662960400+3164896]
	GetHandleVerifier [0x0x7ff662688c3e+185118]
	GetHandleVerifier [0x0x7ff66269054f+216111]
	GetHandleVerifier [0x0x7ff6626772e4+113092]
	GetHandleVerifier [0x0x7ff662677499+113529]
	GetHandleVerifier [0x0x7ff66265e298+10616]
	BaseThreadInitThunk [0x0x7ffd7b95dbe7+23]
	RtlUserThreadStart [0x0x7ffd7bac5a4c+44]

⬇️  Downloaded file: boqcomparativechart (83).xlsx →

In [4]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.ui import WebDriverWait, Select
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import TimeoutException, NoSuchElementException, StaleElementReferenceException
from datetime import datetime
import pandas as pd, os, re, shutil, time

# ───────────────── CONFIG ─────────────────
URL = "https://mptenders.gov.in/nicgep/app?page=WebTenderStatusLists&service=page"
DEPTS = [("MP Water and Land Management Institute", "208")]
published_from = "01/06/2024"
published_to = "30/06/2025"

dept_name_clean = DEPTS[0][0].replace(" ", "_")
OUT_XLSX = f"MP_tenders_{dept_name_clean}_{datetime.today().strftime('%d_%m_%Y')}.xlsx"
DL_ROOT = os.path.join(os.getcwd(), "downloads")
os.makedirs(DL_ROOT, exist_ok=True)
_clean = lambda s: re.sub(r"[^\d.]", "", s.strip())

def dept_dir(name: str) -> str:
    p = os.path.join(DL_ROOT, name)
    os.makedirs(p, exist_ok=True)
    return p

def await_download(before, target_dir, timeout=40):
    WebDriverWait(drv, timeout).until(
        lambda _: any(f.endswith((".xls", ".xlsx", ".pdf")) and not f.endswith(".crdownload")
                      for f in set(os.listdir(DL_ROOT)) - before))
    f = next(x for x in os.listdir(DL_ROOT) if x not in before and not x.endswith(".crdownload"))
    unique_f = f"{int(time.time())}_{f}"
    shutil.move(os.path.join(DL_ROOT, f), os.path.join(target_dir, unique_f))
    print(f"⬇️  Downloaded file: {unique_f} → {target_dir}")

# ───────────── DRIVER ─────────────
opt = webdriver.ChromeOptions()
opt.add_experimental_option("prefs", {
    "download.default_directory": DL_ROOT,
    "download.prompt_for_download": False,
    "safebrowsing.enabled": True
})
drv = webdriver.Chrome(options=opt)
drv.maximize_window()
print(f"📅  {published_from} → {published_to}")

all_rows = []
seen_tids = set()

try:
    drv.get(URL)
    time.sleep(2)

    # CAPTCHA
    open("captcha.png", "wb").write(
        drv.find_element(By.ID, "captchaImage").screenshot_as_png)
    try:
        os.startfile("captcha.png")
    except FileNotFoundError:
        pass
    drv.find_element(By.ID, "captchaText").send_keys(input("Enter CAPTCHA: "))
    print("✅ CAPTCHA solved.\n")

    main_tab = drv.current_window_handle

    # ───────────── MAIN LOOP ─────────────
    for dept, val in DEPTS:
        print(f"🔍 {dept}")
        Select(drv.find_element(By.ID, "OrganName")).select_by_value(val)

        for box, date in [("publishedFromDate", published_from),
                          ("publishedToDate", published_to)]:
            drv.execute_script(
                "document.getElementById(arguments[0]).removeAttribute('readonly');", box)
            elm = drv.find_element(By.ID, box)
            elm.clear()
            elm.send_keys(date)

        drv.find_element(By.ID, "Search").click()
        WebDriverWait(drv, 30).until(
            EC.presence_of_element_located((By.ID, "tabList")))

        try:
            total_info = drv.find_element(By.ID, "totalRecords").text
            print(f"📊 Total records shown on website: {total_info}")
        except Exception as e:
            print(f"⚠️ Could not extract total record count: {e}")

        page = 1
        while True:
            print(f"\n📄 Processing Page {page}")
            rows = drv.find_elements(By.XPATH, "//table[@id='tabList']//tr[td]")
            if len(rows) == 1 and "No Data" in rows[0].text:
                break

            for row in rows:
                try:
                    tds = row.find_elements(By.TAG_NAME, "td")
                    if len(tds) < 6:
                        continue
                    anchors = tds[5].find_elements(By.TAG_NAME, "a")
                    if not anchors:
                        continue

                    sno, tid = [tds[i].text.strip() for i in (0, 1)]
                    if tid in seen_tids:
                        continue
                    seen_tids.add(tid)

                    link = anchors[0]
                    drv.execute_script("arguments[0].setAttribute('target','_blank');", link)
                    link.send_keys(Keys.CONTROL + Keys.RETURN)
                    WebDriverWait(drv, 8).until(lambda d: len(d.window_handles) > 1)
                    detail_tab = [h for h in drv.window_handles if h != main_tab][-1]
                    drv.switch_to.window(detail_tab)

                    WebDriverWait(drv, 8).until(
                        EC.element_to_be_clickable(
                            (By.XPATH, "//a[contains(text(),'View More Details')]"))
                    ).click()

                    remark = "No"
                    save_to = os.path.join(dept_dir(dept), tid)
                    os.makedirs(save_to, exist_ok=True)

                    try:
                        direct = drv.find_elements(
                            By.XPATH,
                            "//a[@id='BOQ' or contains(text(),'BOQ Comparative Chart') or "
                            "contains(@href,'FrontEndViewBidSummaryDetailsPrint')]")
                        if direct:
                            before = set(os.listdir(DL_ROOT))
                            direct[0].click()
                            await_download(before, save_to)
                            remark = "Yes"
                        else:
                            stage_link = WebDriverWait(drv, 6).until(
                                EC.element_to_be_clickable((
                                    By.XPATH, "//a[contains(@onclick,'openPopUp') or "
                                              "starts-with(@id,'DirectLink_')]")))
                            stage_link.send_keys(Keys.CONTROL + Keys.RETURN)
                            WebDriverWait(drv, 6).until(lambda d: len(d.window_handles) > 2)
                            pop = [h for h in drv.window_handles if h not in (main_tab, detail_tab)][0]
                            drv.switch_to.window(pop)
                            chart = WebDriverWait(drv, 8).until(
                                EC.element_to_be_clickable(
                                    (By.XPATH, "//*[@id='BOQ' or starts-with(@id,'CHART')]")))
                            before = set(os.listdir(DL_ROOT))
                            chart.click()
                            await_download(before, save_to)
                            remark = "Yes"
                    except Exception:
                        pass

                    for h in [h for h in drv.window_handles if h != main_tab]:
                        drv.switch_to.window(h)
                        drv.close()
                    drv.switch_to.window(main_tab)

                    all_rows.append({
                        "Department": dept,
                        "S.No": sno,
                        "Tender ID": tid,
                        "Remark": remark
                    })
                    print(f"   ➕ {tid} ({remark})")

                except (StaleElementReferenceException, NoSuchElementException) as e:
                    print(f"⚠️ Skipping a row due to: {e}")
                    continue
                except Exception as e:
                    print(f"⚠️ Error processing tender {tid}: {e}")
                    continue

            print(f"📃 Collected so far: {len(all_rows)} | Page {page}")
            page += 1

            try:
                drv.find_element(By.ID, "loadNext").click()
                WebDriverWait(drv, 8).until(
                    EC.presence_of_element_located((By.ID, "tabList")))
            except Exception:
                print("✅ Finished all pages or no more data.")
                break

finally:
    if all_rows:
        pd.DataFrame(all_rows).to_excel(OUT_XLSX, index=False)
        print(f"\n✅ Rows written: {len(all_rows)} → {OUT_XLSX}")
        print(f"📂 BOQs → {DL_ROOT}/<Department>/<TenderID>/")
    else:
        print("\n⚠️ Script finished but collected ZERO rows — "
              "verify the date filter or that tenders exist.")
    drv.quit()


📅  01/06/2024 → 30/06/2025


Enter CAPTCHA:  6TLYdx


✅ CAPTCHA solved.

🔍 MP Water and Land Management Institute
⚠️ Could not extract total record count: Message: no such element: Unable to locate element: {"method":"css selector","selector":"[id="totalRecords"]"}
  (Session info: chrome=138.0.7204.169); For documentation on this error, please visit: https://www.selenium.dev/documentation/webdriver/troubleshooting/errors#no-such-element-exception
Stacktrace:
	GetHandleVerifier [0x0x7ff66266e935+77845]
	GetHandleVerifier [0x0x7ff66266e990+77936]
	(No symbol) [0x0x7ff662429cda]
	(No symbol) [0x0x7ff6624806aa]
	(No symbol) [0x0x7ff66248095c]
	(No symbol) [0x0x7ff6624d3d07]
	(No symbol) [0x0x7ff6624a890f]
	(No symbol) [0x0x7ff6624d0b07]
	(No symbol) [0x0x7ff6624a86a3]
	(No symbol) [0x0x7ff662471791]
	(No symbol) [0x0x7ff662472523]
	GetHandleVerifier [0x0x7ff66294684d+3059501]
	GetHandleVerifier [0x0x7ff662940c0d+3035885]
	GetHandleVerifier [0x0x7ff662960400+3164896]
	GetHandleVerifier [0x0x7ff662688c3e+185118]
	GetHandleVerifier [0x0x7ff6626

In [2]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.ui import WebDriverWait, Select
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import (
    TimeoutException, NoSuchElementException, StaleElementReferenceException,
)
from datetime import datetime
import pandas as pd, os, re, shutil, time

# ───────────────── CONFIG ─────────────────
URL = ("https://mptenders.gov.in/nicgep/app?page=WebTenderStatusLists&service=page")
DEPTS = [("Public Health Engineering- O/o Engineer In Chief","253")]

published_from = "01/06/2024"  # dd/MM/yyyy format
published_to = "30/06/2025"

# Clean department name to avoid spaces in filename
dept_name_clean = DEPTS[0][0].replace(" ", "_")
OUT_XLSX = f"MP_tenders_{dept_name_clean}_{datetime.today().strftime('%d_%m_%Y')}.xlsx"

DL_ROOT = os.path.join(os.getcwd(), "downloads")
os.makedirs(DL_ROOT, exist_ok=True)
_clean = lambda s: re.sub(r"[^\d.]", "", s.strip())

def dept_dir(name: str) -> str:
    p = os.path.join(DL_ROOT, name)
    os.makedirs(p, exist_ok=True)
    return p

def await_download(before, target_dir, timeout=40):
    WebDriverWait(drv, timeout).until(
        lambda _: any(f.endswith((".xls", ".xlsx", ".pdf")) and not f.endswith(".crdownload")
                      for f in set(os.listdir(DL_ROOT)) - before))
    f = next(x for x in os.listdir(DL_ROOT) if x not in before and not x.endswith(".crdownload"))
    shutil.move(os.path.join(DL_ROOT, f), os.path.join(target_dir, f))
    print(f"⬇️  Downloaded file: {f} → {target_dir}")

# ───────────── DRIVER ─────────────
opt = webdriver.ChromeOptions()
opt.add_experimental_option("prefs", {
    "download.default_directory": DL_ROOT,
    "download.prompt_for_download": False,
    "safebrowsing.enabled": True
})
drv = webdriver.Chrome(options=opt)
drv.maximize_window()
print(f"📅  {published_from} → {published_to}")

all_rows = []
try:
    drv.get(URL)
    time.sleep(2)

    # Manual CAPTCHA - save image and prompt user input
    open("captcha.png", "wb").write(
        drv.find_element(By.ID, "captchaImage").screenshot_as_png)
    try:
        os.startfile("captcha.png")  # Windows only; adjust for others
    except FileNotFoundError:
        pass
    drv.find_element(By.ID, "captchaText").send_keys(input("Enter CAPTCHA: "))
    print("✅ CAPTCHA solved.\n")

    main_tab = drv.current_window_handle

    # ───────────── MAIN LOOP ─────────────
    for dept, val in DEPTS:
        print(f"🔍 {dept}")
        Select(drv.find_element(By.ID, "OrganName")).select_by_value(val)

        for box, date in [("publishedFromDate", published_from),
                          ("publishedToDate", published_to)]:
            drv.execute_script(
                "document.getElementById(arguments[0]).removeAttribute('readonly');", box)
            elm = drv.find_element(By.ID, box)
            elm.clear()
            elm.send_keys(date)

        drv.find_element(By.ID, "Search").click()
        WebDriverWait(drv, 30).until(
            EC.presence_of_element_located((By.ID, "tabList")))

        page = 1
        while True:
            rows = drv.find_elements(By.XPATH, "//table[@id='tabList']//tr[td]")
            if len(rows) == 1 and "No Data" in rows[0].text:
                break

            for row in rows:
                try:
                    tds = row.find_elements(By.TAG_NAME, "td")
                    if len(tds) < 6:
                        continue
                    anchors = tds[5].find_elements(By.TAG_NAME, "a")
                    if not anchors:
                        continue  # skip heading rows

                    sno, tid = [tds[i].text.strip() for i in (0, 1)]

                    # open status in new tab
                    link = anchors[0]
                    drv.execute_script("arguments[0].setAttribute('target','_blank');", link)
                    link.send_keys(Keys.CONTROL + Keys.RETURN)
                    WebDriverWait(drv, 8).until(
                        lambda d: len(d.window_handles) > 1)
                    detail_tab = [h for h in drv.window_handles if h != main_tab][-1]
                    drv.switch_to.window(detail_tab)

                    # View More Details
                    WebDriverWait(drv, 8).until(
                        EC.element_to_be_clickable(
                            (By.XPATH, "//a[contains(text(),'View More Details')]"))
                    ).click()

                    # BOQ
                    remark = "No"
                    save_to = os.path.join(dept_dir(dept), tid)
                    os.makedirs(save_to, exist_ok=True)

                    try:
                        # direct link on detail
                        direct = drv.find_elements(
                            By.XPATH,
                            "//a[@id='BOQ' or contains(text(),'BOQ Comparative Chart') or "
                            "contains(@href,'FrontEndViewBidSummaryDetailsPrint')]")
                        if direct:
                            before = set(os.listdir(DL_ROOT))
                            direct[0].click()
                            await_download(before, save_to)
                            remark = "Yes"
                        else:
                            # stage summary pop-up
                            stage_link = WebDriverWait(drv, 6).until(
                                EC.element_to_be_clickable((
                                    By.XPATH, "//a[contains(@onclick,'openPopUp') or "
                                              "starts-with(@id,'DirectLink_')]")))
                            stage_link.send_keys(Keys.CONTROL + Keys.RETURN)
                            WebDriverWait(drv, 6).until(
                                lambda d: len(d.window_handles) > 2)
                            pop = [h for h in drv.window_handles
                                   if h not in (main_tab, detail_tab)][0]
                            drv.switch_to.window(pop)
                            chart = WebDriverWait(drv, 8).until(
                                EC.element_to_be_clickable(
                                    (By.XPATH, "//*[@id='BOQ' or starts-with(@id,'CHART')]")))
                            before = set(os.listdir(DL_ROOT))
                            chart.click()
                            await_download(before, save_to)
                            remark = "Yes"
                    except Exception:
                        pass

                    # close extra tabs
                    for h in [h for h in drv.window_handles if h != main_tab]:
                        drv.switch_to.window(h)
                        drv.close()
                    drv.switch_to.window(main_tab)

                    all_rows.append({
                        "Department": dept,
                        "S.No": sno,
                        "Tender ID": tid,
                        "Remark": remark
                    })
                    print(f"   ➕ {tid} ({remark})")
                except (StaleElementReferenceException, NoSuchElementException) as e:
                    print(f"⚠️ Skipping a row due to: {e}")
                    continue
                except Exception as e:
                    print(f"⚠️ Error processing tender {tid}: {e}")
                    continue

            print(f"📃 Collected so far: {len(all_rows)} | page {page}")
            page += 1

            # next page
            try:
                drv.find_element(By.ID, "loadNext").click()
                WebDriverWait(drv, 8).until(
                    EC.presence_of_element_located((By.ID, "tabList")))
            except Exception:
                break

finally:
    if all_rows:
        pd.DataFrame(all_rows).to_excel(OUT_XLSX, index=False)
        print(f"\n✅ Rows written: {len(all_rows)} → {OUT_XLSX}")
        print(f"📂 BOQs → {DL_ROOT}/<Department>/<TenderID>/")
    else:
        print("\n⚠️ Script finished but collected ZERO rows — "
              "verify the date filter or that tenders exist.")
    drv.quit()


📅  01/06/2024 → 30/06/2025


Enter CAPTCHA:  kk3e83


✅ CAPTCHA solved.

🔍 Public Health Engineering- O/o Engineer In Chief
   ➕ 2025_PHED_434129_1 (No)
   ➕ 2025_PHED_434114_1 (No)
   ➕ 2025_PHED_434096_1 (No)
   ➕ 2025_PHED_434060_1 (No)
   ➕ 2025_PHED_434049_1 (No)
   ➕ 2025_PHED_434033_1 (No)
   ➕ 2025_PHED_433787_1 (No)
   ➕ 2025_PHED_433785_1 (No)
   ➕ 2025_PHED_433784_1 (No)
   ➕ 2025_PHED_433783_1 (No)
📃 Collected so far: 10 | page 1
   ➕ 2025_PHED_440200_1 (No)
   ➕ 2025_PHED_440199_1 (No)
   ➕ 2025_PHED_440198_1 (No)
   ➕ 2025_PHED_440003_1 (No)
   ➕ 2025_PHED_439990_1 (No)
   ➕ 2025_PHED_439979_1 (No)
   ➕ 2025_PHED_439771_1 (No)
   ➕ 2025_PHED_439769_1 (No)
   ➕ 2025_PHED_439767_1 (No)
   ➕ 2025_PHED_439748_1 (No)
📃 Collected so far: 20 | page 2
   ➕ 2025_PHED_439698_1 (No)
   ➕ 2025_PHED_439657_1 (No)
   ➕ 2025_PHED_439633_1 (No)
   ➕ 2025_PHED_439603_4 (No)
   ➕ 2025_PHED_439603_3 (No)
   ➕ 2025_PHED_439603_2 (No)
   ➕ 2025_PHED_439603_1 (No)
   ➕ 2025_PHED_439591_1 (No)
   ➕ 2025_PHED_439588_1 (No)
   ➕ 2025_PHED_439587_1 (

OSError: Cannot save file into a non-existent directory: 'MP_tenders_Public_Health_Engineering-_O'

In [3]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait, Select
from selenium.webdriver.support import expected_conditions as EC
import pandas as pd
import time, os

# ─── CONFIG ─────────────────────────────────────────────────────────────
URL               = "https://etenders.kerala.gov.in/nicgep/app?page=WebTenderStatusLists&service=page"
DEPARTMENT_VALUE  = "276"   # ← set this to the Assam-specific value
DEPARTMENT_NAME   = "WAPCOS Limited"      # will be populated at runtime
FROM_DATE         = "01/07/2024"
TO_DATE           = "31/07/2025"
OUTPUT_XLS        = "Kerala_PAST_WAPCOS Limited.xlsx"

# ─── BROWSER SETUP ──────────────────────────────────────────────────────
driver = webdriver.Chrome()
driver.maximize_window()
driver.get(URL)
time.sleep(2)

# ─── PICK DEPARTMENT ────────────────────────────────────────────────────
select = Select(driver.find_element(By.ID, "OrganName"))
select.select_by_value(DEPARTMENT_VALUE)
DEPARTMENT_NAME = select.first_selected_option.text.strip()
print(f"🔎 Using Department: {DEPARTMENT_NAME}")

# ─── SET DATE FILTERS ───────────────────────────────────────────────────
for fld_id, val in [("publishedFromDate", FROM_DATE), ("publishedToDate", TO_DATE)]:
    el = driver.find_element(By.ID, fld_id)
    driver.execute_script("arguments[0].removeAttribute('readonly')", el)
    el.clear()
    el.send_keys(val)

# ─── CAPTCHA ───────────────────────────────────────────────────────────
png = "captcha_assam.png"
with open(png, "wb") as f:
    f.write(driver.find_element(By.ID, "captchaImage").screenshot_as_png)
print(f"✔ CAPTCHA saved to {png}. Please open it to read.")
captcha = input("Enter CAPTCHA: ")
driver.find_element(By.ID, "captchaText").send_keys(captcha)
driver.find_element(By.ID, "Search").click()
WebDriverWait(driver, 20).until(EC.presence_of_element_located((By.ID, "tabList")))

# ─── FIELD EXTRACTOR ────────────────────────────────────────────────────
def get_field_value(label):
    target = label.strip().lower()
    captions = driver.find_elements(By.XPATH, "//td[contains(@class,'caption')]")
    for cap in captions:
        if target in cap.text.strip().lower():
            try:
                return cap.find_element(By.XPATH, "following-sibling::td[1]").text.strip()
            except:
                return ""
    return ""

# ─── SCRAPE & PAGINATE ──────────────────────────────────────────────────
all_data = []

while True:
    rows = driver.find_elements(By.XPATH, "//table[@id='tabList']//tr[@class='even' or @class='odd']")
    for idx in range(len(rows)):
        try:
            # refresh row list each iteration
            rows = driver.find_elements(By.XPATH, "//table[@id='tabList']//tr[@class='even' or @class='odd']")
            row = rows[idx]
            cells = row.find_elements(By.TAG_NAME, "td")
            if len(cells) < 6:
                continue

            sno, tid, title, orgs, stage, status = [c.text.strip() for c in cells[:6]]

            # open detail popup
            row.find_element(By.XPATH, ".//td[last()]/a").click()
            WebDriverWait(driver, 10).until(EC.element_to_be_clickable((By.ID, "DirectLink"))).click()
            WebDriverWait(driver, 10).until(lambda d: len(d.window_handles) > 1)
            driver.switch_to.window(driver.window_handles[-1])
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.TAG_NAME, "table")))

            # extract fields
            record = {
                "Department":               DEPARTMENT_NAME,
                "S.No":                     sno.rstrip('.'),
                "Tender ID":                tid,
                "Title & Ref No.":          title,
                "Organisation Chain":       orgs,
                "Tender Stage":             stage,
                "Status":                   status,
                "Publish Date":             get_field_value("Publish Date"),
                "Bid Submission End":       get_field_value("Bid Submission End Date"),
                "Tender Value (₹)":         get_field_value("Tender Value"),
                "Location":                 get_field_value("Location"),
                "Pincode":                  get_field_value("Pincode"),
                "Period Of Work (Days)":    get_field_value("Period Of Work"),
                "Address":                  get_field_value("Address"),
            }
            all_data.append(record)
            print(f"✔ Row {sno}: {tid} extracted")

            # close detail and return to list
            driver.close()
            driver.switch_to.window(driver.window_handles[0])
            WebDriverWait(driver, 10).until(
                EC.element_to_be_clickable((By.XPATH, "//a[contains(text(),'Back')]"))
            ).click()
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.ID, "tabList")))

        except Exception as e:
            print(f"❌ Row {idx+1} error: {e}")
            driver.switch_to.window(driver.window_handles[0])
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.ID, "tabList")))

    # move to next page, if any
    try:
        driver.find_element(By.ID, "loadNext").click()
        WebDriverWait(driver, 20).until(EC.presence_of_element_located((By.ID, "tabList")))
    except:
        break

# ─── EXPORT TO EXCEL ───────────────────────────────────────────────────
df = pd.DataFrame(all_data)
df.to_excel(OUTPUT_XLS, index=False)
print(f"\n✅ Done! Saved {len(all_data)} records to {OUTPUT_XLS}")

driver.quit()


🔎 Using Department: Kerala State Co-operative Employees Welfare Board
✔ CAPTCHA saved to captcha_assam.png. Please open it to read.


Enter CAPTCHA:  4a7YbE



✅ Done! Saved 0 records to Kerala_PAST_WAPCOS Limited.xlsx


In [3]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.ui import WebDriverWait, Select
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import (
    TimeoutException, NoSuchElementException, StaleElementReferenceException,
)
from datetime import datetime
import pandas as pd, os, re, shutil, time

# ───────────────── CONFIG ─────────────────
URL = ("https://etenders.kerala.gov.in/nicgep/app?page=WebTenderStatusLists&service=page")
DEPTS = [("The Kerala Land Development Corporation Ltd","58")]

published_from = "01/07/2024"  # dd/MM/yyyy format
published_to = "31/07/2025"

# Clean department name to avoid spaces in filename
dept_name_clean = DEPTS[0][0].replace(" ", "_")
OUT_XLSX = f"Kerala_tenders_{dept_name_clean}_{datetime.today().strftime('%d_%m_%Y')}.xlsx"

DL_ROOT = os.path.join(os.getcwd(), "downloads")
os.makedirs(DL_ROOT, exist_ok=True)
_clean = lambda s: re.sub(r"[^\d.]", "", s.strip())

def dept_dir(name: str) -> str:
    p = os.path.join(DL_ROOT, name)
    os.makedirs(p, exist_ok=True)
    return p

def await_download(before, target_dir, timeout=40):
    WebDriverWait(drv, timeout).until(
        lambda _: any(f.endswith((".xls", ".xlsx", ".pdf")) and not f.endswith(".crdownload")
                      for f in set(os.listdir(DL_ROOT)) - before))
    f = next(x for x in os.listdir(DL_ROOT) if x not in before and not x.endswith(".crdownload"))
    shutil.move(os.path.join(DL_ROOT, f), os.path.join(target_dir, f))
    print(f"⬇️  Downloaded file: {f} → {target_dir}")

# ───────────── DRIVER ─────────────
opt = webdriver.ChromeOptions()
opt.add_experimental_option("prefs", {
    "download.default_directory": DL_ROOT,
    "download.prompt_for_download": False,
    "safebrowsing.enabled": True
})
drv = webdriver.Chrome(options=opt)
drv.maximize_window()
print(f"📅  {published_from} → {published_to}")

all_rows = []
try:
    drv.get(URL)
    time.sleep(2)

    # Manual CAPTCHA - save image and prompt user input
    open("captcha.png", "wb").write(
        drv.find_element(By.ID, "captchaImage").screenshot_as_png)
    try:
        os.startfile("captcha.png")  # Windows only; adjust for others
    except FileNotFoundError:
        pass
    drv.find_element(By.ID, "captchaText").send_keys(input("Enter CAPTCHA: "))
    print("✅ CAPTCHA solved.\n")

    main_tab = drv.current_window_handle

    # ───────────── MAIN LOOP ─────────────
    for dept, val in DEPTS:
        print(f"🔍 {dept}")
        Select(drv.find_element(By.ID, "OrganName")).select_by_value(val)

        for box, date in [("publishedFromDate", published_from),
                          ("publishedToDate", published_to)]:
            drv.execute_script(
                "document.getElementById(arguments[0]).removeAttribute('readonly');", box)
            elm = drv.find_element(By.ID, box)
            elm.clear()
            elm.send_keys(date)

        drv.find_element(By.ID, "Search").click()
        WebDriverWait(drv, 30).until(
            EC.presence_of_element_located((By.ID, "tabList")))

        page = 1
        while True:
            rows = drv.find_elements(By.XPATH, "//table[@id='tabList']//tr[td]")
            if len(rows) == 1 and "No Data" in rows[0].text:
                break

            for row in rows:
                try:
                    tds = row.find_elements(By.TAG_NAME, "td")
                    if len(tds) < 6:
                        continue
                    anchors = tds[5].find_elements(By.TAG_NAME, "a")
                    if not anchors:
                        continue  # skip heading rows

                    sno, tid = [tds[i].text.strip() for i in (0, 1)]

                    # open status in new tab
                    link = anchors[0]
                    drv.execute_script("arguments[0].setAttribute('target','_blank');", link)
                    link.send_keys(Keys.CONTROL + Keys.RETURN)
                    WebDriverWait(drv, 8).until(
                        lambda d: len(d.window_handles) > 1)
                    detail_tab = [h for h in drv.window_handles if h != main_tab][-1]
                    drv.switch_to.window(detail_tab)

                    # View More Details
                    WebDriverWait(drv, 8).until(
                        EC.element_to_be_clickable(
                            (By.XPATH, "//a[contains(text(),'View More Details')]"))
                    ).click()

                    # BOQ
                    remark = "No"
                    save_to = os.path.join(dept_dir(dept), tid)
                    os.makedirs(save_to, exist_ok=True)

                    try:
                        # direct link on detail
                        direct = drv.find_elements(
                            By.XPATH,
                            "//a[@id='BOQ' or contains(text(),'BOQ Comparative Chart') or "
                            "contains(@href,'FrontEndViewBidSummaryDetailsPrint')]")
                        if direct:
                            before = set(os.listdir(DL_ROOT))
                            direct[0].click()
                            await_download(before, save_to)
                            remark = "Yes"
                        else:
                            # stage summary pop-up
                            stage_link = WebDriverWait(drv, 6).until(
                                EC.element_to_be_clickable((
                                    By.XPATH, "//a[contains(@onclick,'openPopUp') or "
                                              "starts-with(@id,'DirectLink_')]")))
                            stage_link.send_keys(Keys.CONTROL + Keys.RETURN)
                            WebDriverWait(drv, 6).until(
                                lambda d: len(d.window_handles) > 2)
                            pop = [h for h in drv.window_handles
                                   if h not in (main_tab, detail_tab)][0]
                            drv.switch_to.window(pop)
                            chart = WebDriverWait(drv, 8).until(
                                EC.element_to_be_clickable(
                                    (By.XPATH, "//*[@id='BOQ' or starts-with(@id,'CHART')]")))
                            before = set(os.listdir(DL_ROOT))
                            chart.click()
                            await_download(before, save_to)
                            remark = "Yes"
                    except Exception:
                        pass

                    # close extra tabs
                    for h in [h for h in drv.window_handles if h != main_tab]:
                        drv.switch_to.window(h)
                        drv.close()
                    drv.switch_to.window(main_tab)

                    all_rows.append({
                        "Department": dept,
                        "S.No": sno,
                        "Tender ID": tid,
                        "Remark": remark
                    })
                    print(f"   ➕ {tid} ({remark})")
                except (StaleElementReferenceException, NoSuchElementException) as e:
                    print(f"⚠️ Skipping a row due to: {e}")
                    continue
                except Exception as e:
                    print(f"⚠️ Error processing tender {tid}: {e}")
                    continue

            print(f"📃 Collected so far: {len(all_rows)} | page {page}")
            page += 1

            # next page
            try:
                drv.find_element(By.ID, "loadNext").click()
                WebDriverWait(drv, 8).until(
                    EC.presence_of_element_located((By.ID, "tabList")))
            except Exception:
                break

finally:
    if all_rows:
        pd.DataFrame(all_rows).to_excel(OUT_XLSX, index=False)
        print(f"\n✅ Rows written: {len(all_rows)} → {OUT_XLSX}")
        print(f"📂 BOQs → {DL_ROOT}/<Department>/<TenderID>/")
    else:
        print("\n⚠️ Script finished but collected ZERO rows — "
              "verify the date filter or that tenders exist.")
    drv.quit()


📅  01/07/2024 → 31/07/2025


Enter CAPTCHA:  bYXCt6


✅ CAPTCHA solved.

🔍 The Kerala Land Development Corporation Ltd
   ➕ 2025_CEI_736820_1 (No)
   ➕ 2025_CEI_731348_1 (No)
   ➕ 2025_CEI_723432_1 (No)
   ➕ 2025_CEI_723356_1 (No)
   ➕ 2025_CEI_723321_1 (No)
   ➕ 2024_CEI_716722_1 (No)
   ➕ 2024_CEI_716704_1 (No)
   ➕ 2024_CEI_712530_1 (No)
   ➕ 2024_CEI_707117_1 (No)
   ➕ 2024_CEI_690729_2 (No)
📃 Collected so far: 10 | page 1
   ➕ 2024_CEI_690729_1 (No)
   ➕ 2023_CEI_613082_2 (No)
   ➕ 2023_CEI_613082_1 (No)
⬇️  Downloaded file: boqcomparativechart - 2025-07-31T124619.763.xlsx → C:\Users\Jaydeb\downloads\The Kerala Land Development Corporation Ltd\2022_CEI_520285_1
   ➕ 2022_CEI_520285_1 (Yes)
⬇️  Downloaded file: boqcomparativechart - 2025-07-31T124621.953.xlsx → C:\Users\Jaydeb\downloads\The Kerala Land Development Corporation Ltd\2022_CEI_501021_2
   ➕ 2022_CEI_501021_2 (Yes)
   ➕ 2022_CEI_501021_1 (No)
⬇️  Downloaded file: boqcomparativechart - 2025-07-31T124633.217.xlsx → C:\Users\Jaydeb\downloads\The Kerala Land Development Corpora

In [7]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait, Select
from selenium.webdriver.support import expected_conditions as EC
import pandas as pd
import time, os

# ─── CONFIG ─────────────────────────────────────────────────────────────
URL               = "https://tntenders.gov.in/nicgep/app?page=WebTenderStatusLists&service=page"
DEPARTMENT_VALUE  = "227"   # ← set this to the Assam-specific value
DEPARTMENT_NAME   = "Water Resources Department"      # will be populated at runtime
FROM_DATE         = "01/07/2024"
TO_DATE           = "31/07/2025"
OUTPUT_XLS        = "Tamilnadu_PAST_Water Resources Department.xlsx"

# ─── BROWSER SETUP ──────────────────────────────────────────────────────
driver = webdriver.Chrome()
driver.maximize_window()
driver.get(URL)
time.sleep(2)

# ─── PICK DEPARTMENT ────────────────────────────────────────────────────
select = Select(driver.find_element(By.ID, "OrganName"))
select.select_by_value(DEPARTMENT_VALUE)
DEPARTMENT_NAME = select.first_selected_option.text.strip()
print(f"🔎 Using Department: {DEPARTMENT_NAME}")

# ─── SET DATE FILTERS ───────────────────────────────────────────────────
for fld_id, val in [("publishedFromDate", FROM_DATE), ("publishedToDate", TO_DATE)]:
    el = driver.find_element(By.ID, fld_id)
    driver.execute_script("arguments[0].removeAttribute('readonly')", el)
    el.clear()
    el.send_keys(val)

# ─── CAPTCHA ───────────────────────────────────────────────────────────
png = "captcha_assam.png"
with open(png, "wb") as f:
    f.write(driver.find_element(By.ID, "captchaImage").screenshot_as_png)
print(f"✔ CAPTCHA saved to {png}. Please open it to read.")
captcha = input("Enter CAPTCHA: ")
driver.find_element(By.ID, "captchaText").send_keys(captcha)
driver.find_element(By.ID, "Search").click()
WebDriverWait(driver, 20).until(EC.presence_of_element_located((By.ID, "tabList")))

# ─── FIELD EXTRACTOR ────────────────────────────────────────────────────
def get_field_value(label):
    target = label.strip().lower()
    captions = driver.find_elements(By.XPATH, "//td[contains(@class,'caption')]")
    for cap in captions:
        if target in cap.text.strip().lower():
            try:
                return cap.find_element(By.XPATH, "following-sibling::td[1]").text.strip()
            except:
                return ""
    return ""

# ─── SCRAPE & PAGINATE ──────────────────────────────────────────────────
all_data = []

while True:
    rows = driver.find_elements(By.XPATH, "//table[@id='tabList']//tr[@class='even' or @class='odd']")
    for idx in range(len(rows)):
        try:
            # refresh row list each iteration
            rows = driver.find_elements(By.XPATH, "//table[@id='tabList']//tr[@class='even' or @class='odd']")
            row = rows[idx]
            cells = row.find_elements(By.TAG_NAME, "td")
            if len(cells) < 6:
                continue

            sno, tid, title, orgs, stage, status = [c.text.strip() for c in cells[:6]]

            # open detail popup
            row.find_element(By.XPATH, ".//td[last()]/a").click()
            WebDriverWait(driver, 10).until(EC.element_to_be_clickable((By.ID, "DirectLink"))).click()
            WebDriverWait(driver, 10).until(lambda d: len(d.window_handles) > 1)
            driver.switch_to.window(driver.window_handles[-1])
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.TAG_NAME, "table")))

            # extract fields
            record = {
                "Department":               DEPARTMENT_NAME,
                "S.No":                     sno.rstrip('.'),
                "Tender ID":                tid,
                "Title & Ref No.":          title,
                "Organisation Chain":       orgs,
                "Tender Stage":             stage,
                "Status":                   status,
                "Publish Date":             get_field_value("Publish Date"),
                "Bid Submission End":       get_field_value("Bid Submission End Date"),
                "Tender Value (₹)":         get_field_value("Tender Value"),
                "Location":                 get_field_value("Location"),
                "Pincode":                  get_field_value("Pincode"),
                "Period Of Work (Days)":    get_field_value("Period Of Work"),
                "Address":                  get_field_value("Address"),
            }
            all_data.append(record)
            print(f"✔ Row {sno}: {tid} extracted")

            # close detail and return to list
            driver.close()
            driver.switch_to.window(driver.window_handles[0])
            WebDriverWait(driver, 10).until(
                EC.element_to_be_clickable((By.XPATH, "//a[contains(text(),'Back')]"))
            ).click()
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.ID, "tabList")))

        except Exception as e:
            print(f"❌ Row {idx+1} error: {e}")
            driver.switch_to.window(driver.window_handles[0])
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.ID, "tabList")))

    # move to next page, if any
    try:
        driver.find_element(By.ID, "loadNext").click()
        WebDriverWait(driver, 20).until(EC.presence_of_element_located((By.ID, "tabList")))
    except:
        break

# ─── EXPORT TO EXCEL ───────────────────────────────────────────────────
df = pd.DataFrame(all_data)
df.to_excel(OUTPUT_XLS, index=False)
print(f"\n✅ Done! Saved {len(all_data)} records to {OUTPUT_XLS}")

driver.quit()


🔎 Using Department: Water Resources Department
✔ CAPTCHA saved to captcha_assam.png. Please open it to read.


Enter CAPTCHA:  3BFx8D


✔ Row 1.: 2025_WRD_583291_1 extracted
✔ Row 2.: 2025_WRD_575048_1 extracted
✔ Row 3.: 2025_WRD_569769_1 extracted
✔ Row 4.: 2025_WRD_569280_1 extracted
✔ Row 5.: 2025_WRD_569278_1 extracted
✔ Row 6.: 2025_WRD_569274_1 extracted
✔ Row 7.: 2025_WRD_569271_1 extracted
✔ Row 8.: 2025_WRD_569270_1 extracted
✔ Row 9.: 2025_WRD_569268_1 extracted
✔ Row 10.: 2025_WRD_569267_1 extracted
✔ Row 11.: 2025_WRD_569263_1 extracted
✔ Row 12.: 2025_WRD_569239_1 extracted
✔ Row 13.: 2025_WRD_569231_1 extracted
✔ Row 14.: 2025_WRD_569218_1 extracted
✔ Row 15.: 2025_WRD_569197_1 extracted
✔ Row 16.: 2025_WRD_569172_1 extracted
✔ Row 17.: 2025_WRD_569133_1 extracted
✔ Row 18.: 2025_WRD_566201_1 extracted
✔ Row 19.: 2025_WRD_564918_1 extracted
✔ Row 20.: 2025_WRD_562076_1 extracted
✔ Row 21.: 2025_WRD_561895_1 extracted
✔ Row 22.: 2025_WRD_559674_1 extracted
✔ Row 23.: 2025_WRD_559667_1 extracted
✔ Row 24.: 2025_WRD_559652_1 extracted
✔ Row 25.: 2025_WRD_559644_1 extracted
✔ Row 26.: 2025_WRD_559628_1 extra

In [1]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.ui import WebDriverWait, Select
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import (
    TimeoutException, NoSuchElementException, StaleElementReferenceException,
)
from datetime import datetime
import pandas as pd, os, re, shutil, time

# ───────────────── CONFIG ─────────────────
URL = ("https://tntenders.gov.in/nicgep/app?page=WebTenderStatusLists&service=page")
DEPTS = [("Rural Development and Panchayat Raj Department","123")]

published_from = "01/07/2024"  # dd/MM/yyyy format
published_to = "31/07/2025"

# Clean department name to avoid spaces in filename
dept_name_clean = DEPTS[0][0].replace(" ", "_")
OUT_XLSX = f"Tamilnadu_tenders_{dept_name_clean}_{datetime.today().strftime('%d_%m_%Y')}.xlsx"

DL_ROOT = os.path.join(os.getcwd(), "downloads")
os.makedirs(DL_ROOT, exist_ok=True)
_clean = lambda s: re.sub(r"[^\d.]", "", s.strip())

def dept_dir(name: str) -> str:
    p = os.path.join(DL_ROOT, name)
    os.makedirs(p, exist_ok=True)
    return p

def await_download(before, target_dir, timeout=40):
    WebDriverWait(drv, timeout).until(
        lambda _: any(f.endswith((".xls", ".xlsx", ".pdf")) and not f.endswith(".crdownload")
                      for f in set(os.listdir(DL_ROOT)) - before))
    f = next(x for x in os.listdir(DL_ROOT) if x not in before and not x.endswith(".crdownload"))
    shutil.move(os.path.join(DL_ROOT, f), os.path.join(target_dir, f))
    print(f"⬇️  Downloaded file: {f} → {target_dir}")

# ───────────── DRIVER ─────────────
opt = webdriver.ChromeOptions()
opt.add_experimental_option("prefs", {
    "download.default_directory": DL_ROOT,
    "download.prompt_for_download": False,
    "safebrowsing.enabled": True
})
drv = webdriver.Chrome(options=opt)
drv.maximize_window()
print(f"📅  {published_from} → {published_to}")

all_rows = []
try:
    drv.get(URL)
    time.sleep(2)

    # Manual CAPTCHA - save image and prompt user input
    open("captcha.png", "wb").write(
        drv.find_element(By.ID, "captchaImage").screenshot_as_png)
    try:
        os.startfile("captcha.png")  # Windows only; adjust for others
    except FileNotFoundError:
        pass
    drv.find_element(By.ID, "captchaText").send_keys(input("Enter CAPTCHA: "))
    print("✅ CAPTCHA solved.\n")

    main_tab = drv.current_window_handle

    # ───────────── MAIN LOOP ─────────────
    for dept, val in DEPTS:
        print(f"🔍 {dept}")
        Select(drv.find_element(By.ID, "OrganName")).select_by_value(val)

        for box, date in [("publishedFromDate", published_from),
                          ("publishedToDate", published_to)]:
            drv.execute_script(
                "document.getElementById(arguments[0]).removeAttribute('readonly');", box)
            elm = drv.find_element(By.ID, box)
            elm.clear()
            elm.send_keys(date)

        drv.find_element(By.ID, "Search").click()
        WebDriverWait(drv, 30).until(
            EC.presence_of_element_located((By.ID, "tabList")))

        page = 1
        while True:
            rows = drv.find_elements(By.XPATH, "//table[@id='tabList']//tr[td]")
            if len(rows) == 1 and "No Data" in rows[0].text:
                break

            for row in rows:
                try:
                    tds = row.find_elements(By.TAG_NAME, "td")
                    if len(tds) < 6:
                        continue
                    anchors = tds[5].find_elements(By.TAG_NAME, "a")
                    if not anchors:
                        continue  # skip heading rows

                    sno, tid = [tds[i].text.strip() for i in (0, 1)]

                    # open status in new tab
                    link = anchors[0]
                    drv.execute_script("arguments[0].setAttribute('target','_blank');", link)
                    link.send_keys(Keys.CONTROL + Keys.RETURN)
                    WebDriverWait(drv, 8).until(
                        lambda d: len(d.window_handles) > 1)
                    detail_tab = [h for h in drv.window_handles if h != main_tab][-1]
                    drv.switch_to.window(detail_tab)

                    # View More Details
                    WebDriverWait(drv, 8).until(
                        EC.element_to_be_clickable(
                            (By.XPATH, "//a[contains(text(),'View More Details')]"))
                    ).click()

                    # BOQ
                    remark = "No"
                    save_to = os.path.join(dept_dir(dept), tid)
                    os.makedirs(save_to, exist_ok=True)

                    try:
                        # direct link on detail
                        direct = drv.find_elements(
                            By.XPATH,
                            "//a[@id='BOQ' or contains(text(),'BOQ Comparative Chart') or "
                            "contains(@href,'FrontEndViewBidSummaryDetailsPrint')]")
                        if direct:
                            before = set(os.listdir(DL_ROOT))
                            direct[0].click()
                            await_download(before, save_to)
                            remark = "Yes"
                        else:
                            # stage summary pop-up
                            stage_link = WebDriverWait(drv, 6).until(
                                EC.element_to_be_clickable((
                                    By.XPATH, "//a[contains(@onclick,'openPopUp') or "
                                              "starts-with(@id,'DirectLink_')]")))
                            stage_link.send_keys(Keys.CONTROL + Keys.RETURN)
                            WebDriverWait(drv, 6).until(
                                lambda d: len(d.window_handles) > 2)
                            pop = [h for h in drv.window_handles
                                   if h not in (main_tab, detail_tab)][0]
                            drv.switch_to.window(pop)
                            chart = WebDriverWait(drv, 8).until(
                                EC.element_to_be_clickable(
                                    (By.XPATH, "//*[@id='BOQ' or starts-with(@id,'CHART')]")))
                            before = set(os.listdir(DL_ROOT))
                            chart.click()
                            await_download(before, save_to)
                            remark = "Yes"
                    except Exception:
                        pass

                    # close extra tabs
                    for h in [h for h in drv.window_handles if h != main_tab]:
                        drv.switch_to.window(h)
                        drv.close()
                    drv.switch_to.window(main_tab)

                    all_rows.append({
                        "Department": dept,
                        "S.No": sno,
                        "Tender ID": tid,
                        "Remark": remark
                    })
                    print(f"   ➕ {tid} ({remark})")
                except (StaleElementReferenceException, NoSuchElementException) as e:
                    print(f"⚠️ Skipping a row due to: {e}")
                    continue
                except Exception as e:
                    print(f"⚠️ Error processing tender {tid}: {e}")
                    continue

            print(f"📃 Collected so far: {len(all_rows)} | page {page}")
            page += 1

            # next page
            try:
                drv.find_element(By.ID, "loadNext").click()
                WebDriverWait(drv, 8).until(
                    EC.presence_of_element_located((By.ID, "tabList")))
            except Exception:
                break

finally:
    if all_rows:
        pd.DataFrame(all_rows).to_excel(OUT_XLSX, index=False)
        print(f"\n✅ Rows written: {len(all_rows)} → {OUT_XLSX}")
        print(f"📂 BOQs → {DL_ROOT}/<Department>/<TenderID>/")
    else:
        print("\n⚠️ Script finished but collected ZERO rows — "
              "verify the date filter or that tenders exist.")
    drv.quit()


📅  01/07/2024 → 31/07/2025


Enter CAPTCHA:  an5L3L


✅ CAPTCHA solved.

🔍 Rural Development and Panchayat Raj Department
   ➕ 2025_RDTN_587674_1 (No)
   ➕ 2025_RDTN_587667_1 (No)
   ➕ 2025_RDTN_587661_1 (No)
   ➕ 2025_RDTN_587658_1 (No)
   ➕ 2025_RDTN_587649_1 (No)
   ➕ 2025_RDTN_587645_1 (No)
   ➕ 2025_RDTN_587640_3 (No)
   ➕ 2025_RDTN_587640_2 (No)
   ➕ 2025_RDTN_587640_1 (No)
   ➕ 2025_RDTN_587638_1 (No)
📃 Collected so far: 10 | page 1
   ➕ 2025_RDTN_587637_1 (No)
   ➕ 2025_RDTN_587636_1 (No)
   ➕ 2025_RDTN_587632_1 (No)
   ➕ 2025_RDTN_587624_1 (No)
   ➕ 2025_RDTN_587615_1 (No)
   ➕ 2025_RDTN_587610_1 (No)
   ➕ 2025_RDTN_587604_1 (No)
   ➕ 2025_RDTN_587598_1 (No)
   ➕ 2025_RDTN_587595_1 (No)
   ➕ 2025_RDTN_587586_1 (No)
📃 Collected so far: 20 | page 2
   ➕ 2025_RDTN_587585_1 (No)
   ➕ 2025_RDTN_587574_1 (No)
   ➕ 2025_RDTN_587567_1 (No)
   ➕ 2025_RDTN_587565_1 (No)
   ➕ 2025_RDTN_587552_1 (No)
   ➕ 2025_RDTN_587545_1 (No)
   ➕ 2025_RDTN_587543_1 (No)
   ➕ 2025_RDTN_587542_1 (No)
   ➕ 2025_RDTN_587537_1 (No)
   ➕ 2025_RDTN_587533_1 (No

In [1]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait, Select
from selenium.webdriver.support import expected_conditions as EC
import pandas as pd
import time, os

# ─── CONFIG ─────────────────────────────────────────────────────────────
URL               = "https://eproc.rajasthan.gov.in/nicgep/app?page=WebTenderStatusLists&service=page"
DEPARTMENT_VALUE  = "42"   # ← set this to the Assam-specific value
DEPARTMENT_NAME   = "Deptt. of Watershed Dev. and Soil Conservation"      # will be populated at runtime
FROM_DATE         = "01/07/2024"
TO_DATE           = "31/07/2025"
OUTPUT_XLS        = "Rajasthan_PAST_Deptt. of Watershed Dev. and Soil Conservation.xlsx"

# ─── BROWSER SETUP ──────────────────────────────────────────────────────
driver = webdriver.Chrome()
driver.maximize_window()
driver.get(URL)
time.sleep(2)

# ─── PICK DEPARTMENT ────────────────────────────────────────────────────
select = Select(driver.find_element(By.ID, "OrganName"))
select.select_by_value(DEPARTMENT_VALUE)
DEPARTMENT_NAME = select.first_selected_option.text.strip()
print(f"🔎 Using Department: {DEPARTMENT_NAME}")

# ─── SET DATE FILTERS ───────────────────────────────────────────────────
for fld_id, val in [("publishedFromDate", FROM_DATE), ("publishedToDate", TO_DATE)]:
    el = driver.find_element(By.ID, fld_id)
    driver.execute_script("arguments[0].removeAttribute('readonly')", el)
    el.clear()
    el.send_keys(val)

# ─── CAPTCHA ───────────────────────────────────────────────────────────
png = "captcha_Rajasthan.png"
with open(png, "wb") as f:
    f.write(driver.find_element(By.ID, "captchaImage").screenshot_as_png)
print(f"✔ CAPTCHA saved to {png}. Please open it to read.")
captcha = input("Enter CAPTCHA: ")
driver.find_element(By.ID, "captchaText").send_keys(captcha)
driver.find_element(By.ID, "Search").click()
WebDriverWait(driver, 20).until(EC.presence_of_element_located((By.ID, "tabList")))

# ─── FIELD EXTRACTOR ────────────────────────────────────────────────────
def get_field_value(label):
    target = label.strip().lower()
    captions = driver.find_elements(By.XPATH, "//td[contains(@class,'caption')]")
    for cap in captions:
        if target in cap.text.strip().lower():
            try:
                return cap.find_element(By.XPATH, "following-sibling::td[1]").text.strip()
            except:
                return ""
    return ""

# ─── SCRAPE & PAGINATE ──────────────────────────────────────────────────
all_data = []

while True:
    rows = driver.find_elements(By.XPATH, "//table[@id='tabList']//tr[@class='even' or @class='odd']")
    for idx in range(len(rows)):
        try:
            # refresh row list each iteration
            rows = driver.find_elements(By.XPATH, "//table[@id='tabList']//tr[@class='even' or @class='odd']")
            row = rows[idx]
            cells = row.find_elements(By.TAG_NAME, "td")
            if len(cells) < 6:
                continue

            sno, tid, title, orgs, stage, status = [c.text.strip() for c in cells[:6]]

            # open detail popup
            row.find_element(By.XPATH, ".//td[last()]/a").click()
            WebDriverWait(driver, 10).until(EC.element_to_be_clickable((By.ID, "DirectLink"))).click()
            WebDriverWait(driver, 10).until(lambda d: len(d.window_handles) > 1)
            driver.switch_to.window(driver.window_handles[-1])
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.TAG_NAME, "table")))

            # extract fields
            record = {
                "Department":               DEPARTMENT_NAME,
                "S.No":                     sno.rstrip('.'),
                "Tender ID":                tid,
                "Title & Ref No.":          title,
                "Organisation Chain":       orgs,
                "Tender Stage":             stage,
                "Status":                   status,
                "Publish Date":             get_field_value("Publish Date"),
                "Bid Submission End":       get_field_value("Bid Submission End Date"),
                "Tender Value (₹)":         get_field_value("Tender Value"),
                "Location":                 get_field_value("Location"),
                "Pincode":                  get_field_value("Pincode"),
                "Period Of Work (Days)":    get_field_value("Period Of Work"),
                "Address":                  get_field_value("Address"),
            }
            all_data.append(record)
            print(f"✔ Row {sno}: {tid} extracted")

            # close detail and return to list
            driver.close()
            driver.switch_to.window(driver.window_handles[0])
            WebDriverWait(driver, 10).until(
                EC.element_to_be_clickable((By.XPATH, "//a[contains(text(),'Back')]"))
            ).click()
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.ID, "tabList")))

        except Exception as e:
            print(f"❌ Row {idx+1} error: {e}")
            driver.switch_to.window(driver.window_handles[0])
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.ID, "tabList")))

    # move to next page, if any
    try:
        driver.find_element(By.ID, "loadNext").click()
        WebDriverWait(driver, 20).until(EC.presence_of_element_located((By.ID, "tabList")))
    except:
        break

# ─── EXPORT TO EXCEL ───────────────────────────────────────────────────
df = pd.DataFrame(all_data)
df.to_excel(OUTPUT_XLS, index=False)
print(f"\n✅ Done! Saved {len(all_data)} records to {OUTPUT_XLS}")

driver.quit()


🔎 Using Department: Deptt. of Watershed Dev. and Soil Conservation
✔ CAPTCHA saved to captcha_Rajasthan.png. Please open it to read.


Enter CAPTCHA:  6Zktv7


✔ Row 1.: 2025_WDSC_491471_8 extracted
✔ Row 2.: 2025_WDSC_491471_7 extracted
✔ Row 3.: 2025_WDSC_491471_6 extracted
✔ Row 4.: 2025_WDSC_491471_5 extracted
✔ Row 5.: 2025_WDSC_491471_4 extracted
✔ Row 6.: 2025_WDSC_491471_3 extracted
✔ Row 7.: 2025_WDSC_491471_2 extracted
✔ Row 8.: 2025_WDSC_491471_1 extracted
✔ Row 9.: 2025_WDSC_491470_1 extracted
✔ Row 10.: 2025_WDSC_491464_1 extracted
✔ Row 11.: 2025_WDSC_491334_2 extracted
✔ Row 12.: 2025_WDSC_491334_1 extracted
✔ Row 13.: 2025_WDSC_491256_3 extracted
✔ Row 14.: 2025_WDSC_491256_2 extracted
✔ Row 15.: 2025_WDSC_491256_1 extracted
✔ Row 16.: 2025_WDSC_491219_1 extracted
✔ Row 17.: 2025_WDSC_491216_1 extracted
✔ Row 18.: 2025_WDSC_491163_1 extracted
✔ Row 19.: 2025_WDSC_491150_1 extracted
✔ Row 20.: 2025_WDSC_491125_1 extracted
✔ Row 21.: 2025_WDSC_491104_1 extracted
✔ Row 22.: 2025_WDSC_490921_1 extracted
✔ Row 23.: 2025_WDSC_490894_1 extracted
✔ Row 24.: 2025_WDSC_490780_4 extracted
✔ Row 25.: 2025_WDSC_490780_3 extracted
✔ Row 26.

In [1]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait, Select
from selenium.webdriver.support import expected_conditions as EC
import pandas as pd
import time, os

# ─── CONFIG ─────────────────────────────────────────────────────────────
URL               = "https://wbtenders.gov.in/nicgep/app?page=WebTenderStatusLists&service=page"
DEPARTMENT_VALUE  = "209"   # ← set this to the Assam-specific value
DEPARTMENT_NAME   = "PHE"      # will be populated at runtime
FROM_DATE         = "01/07/2024"
TO_DATE           = "31/07/2025"
OUTPUT_XLS        = "WB_PAST_PHE.xlsx"

# ─── BROWSER SETUP ──────────────────────────────────────────────────────
driver = webdriver.Chrome()
driver.maximize_window()
driver.get(URL)
time.sleep(2)

# ─── PICK DEPARTMENT ────────────────────────────────────────────────────
select = Select(driver.find_element(By.ID, "OrganName"))
select.select_by_value(DEPARTMENT_VALUE)
DEPARTMENT_NAME = select.first_selected_option.text.strip()
print(f"🔎 Using Department: {DEPARTMENT_NAME}")

# ─── SET DATE FILTERS ───────────────────────────────────────────────────
for fld_id, val in [("publishedFromDate", FROM_DATE), ("publishedToDate", TO_DATE)]:
    el = driver.find_element(By.ID, fld_id)
    driver.execute_script("arguments[0].removeAttribute('readonly')", el)
    el.clear()
    el.send_keys(val)

# ─── CAPTCHA ───────────────────────────────────────────────────────────
png = "captcha_WB.png"
with open(png, "wb") as f:
    f.write(driver.find_element(By.ID, "captchaImage").screenshot_as_png)
print(f"✔ CAPTCHA saved to {png}. Please open it to read.")
captcha = input("Enter CAPTCHA: ")
driver.find_element(By.ID, "captchaText").send_keys(captcha)
driver.find_element(By.ID, "Search").click()
WebDriverWait(driver, 20).until(EC.presence_of_element_located((By.ID, "tabList")))

# ─── FIELD EXTRACTOR ────────────────────────────────────────────────────
def get_field_value(label):
    target = label.strip().lower()
    captions = driver.find_elements(By.XPATH, "//td[contains(@class,'caption')]")
    for cap in captions:
        if target in cap.text.strip().lower():
            try:
                return cap.find_element(By.XPATH, "following-sibling::td[1]").text.strip()
            except:
                return ""
    return ""

# ─── SCRAPE & PAGINATE ──────────────────────────────────────────────────
all_data = []

while True:
    rows = driver.find_elements(By.XPATH, "//table[@id='tabList']//tr[@class='even' or @class='odd']")
    for idx in range(len(rows)):
        try:
            # refresh row list each iteration
            rows = driver.find_elements(By.XPATH, "//table[@id='tabList']//tr[@class='even' or @class='odd']")
            row = rows[idx]
            cells = row.find_elements(By.TAG_NAME, "td")
            if len(cells) < 6:
                continue

            sno, tid, title, orgs, stage, status = [c.text.strip() for c in cells[:6]]

            # open detail popup
            row.find_element(By.XPATH, ".//td[last()]/a").click()
            WebDriverWait(driver, 10).until(EC.element_to_be_clickable((By.ID, "DirectLink"))).click()
            WebDriverWait(driver, 10).until(lambda d: len(d.window_handles) > 1)
            driver.switch_to.window(driver.window_handles[-1])
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.TAG_NAME, "table")))

            # extract fields
            record = {
                "Department":               DEPARTMENT_NAME,
                "S.No":                     sno.rstrip('.'),
                "Tender ID":                tid,
                "Title & Ref No.":          title,
                "Organisation Chain":       orgs,
                "Tender Stage":             stage,
                "Status":                   status,
                "Publish Date":             get_field_value("Publish Date"),
                "Bid Submission End":       get_field_value("Bid Submission End Date"),
                "Tender Value (₹)":         get_field_value("Tender Value"),
                "Location":                 get_field_value("Location"),
                "Pincode":                  get_field_value("Pincode"),
                "Period Of Work (Days)":    get_field_value("Period Of Work"),
                "Address":                  get_field_value("Address"),
            }
            all_data.append(record)
            print(f"✔ Row {sno}: {tid} extracted")

            # close detail and return to list
            driver.close()
            driver.switch_to.window(driver.window_handles[0])
            WebDriverWait(driver, 10).until(
                EC.element_to_be_clickable((By.XPATH, "//a[contains(text(),'Back')]"))
            ).click()
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.ID, "tabList")))

        except Exception as e:
            print(f"❌ Row {idx+1} error: {e}")
            driver.switch_to.window(driver.window_handles[0])
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.ID, "tabList")))

    # move to next page, if any
    try:
        driver.find_element(By.ID, "loadNext").click()
        WebDriverWait(driver, 20).until(EC.presence_of_element_located((By.ID, "tabList")))
    except:
        break

# ─── EXPORT TO EXCEL ───────────────────────────────────────────────────
df = pd.DataFrame(all_data)
df.to_excel(OUTPUT_XLS, index=False)
print(f"\n✅ Done! Saved {len(all_data)} records to {OUTPUT_XLS}")

driver.quit()


🔎 Using Department: PHE
✔ CAPTCHA saved to captcha_WB.png. Please open it to read.


Enter CAPTCHA:  8nJ2Pz


✔ Row 1.: 2025_PHED_885801_5 extracted
✔ Row 2.: 2025_PHED_885801_4 extracted
✔ Row 3.: 2025_PHED_885801_3 extracted
✔ Row 4.: 2025_PHED_885801_2 extracted
✔ Row 5.: 2025_PHED_885801_1 extracted
✔ Row 6.: 2025_PHED_885780_2 extracted
✔ Row 7.: 2025_PHED_885780_1 extracted
✔ Row 8.: 2025_PHED_885621_2 extracted
✔ Row 9.: 2025_PHED_885621_1 extracted
✔ Row 10.: 2025_PHED_885613_1 extracted
✔ Row 11.: 2025_PHED_885606_5 extracted
✔ Row 12.: 2025_PHED_885606_4 extracted
✔ Row 13.: 2025_PHED_885606_3 extracted
✔ Row 14.: 2025_PHED_885606_2 extracted
✔ Row 15.: 2025_PHED_885606_1 extracted
✔ Row 16.: 2025_PHED_885403_2 extracted
✔ Row 17.: 2025_PHED_885403_1 extracted
✔ Row 18.: 2025_PHED_885272_5 extracted
✔ Row 19.: 2025_PHED_885272_4 extracted
✔ Row 20.: 2025_PHED_885272_3 extracted
✔ Row 21.: 2025_PHED_885272_2 extracted
✔ Row 22.: 2025_PHED_885272_1 extracted
✔ Row 23.: 2025_PHED_885259_3 extracted
✔ Row 24.: 2025_PHED_885259_2 extracted
✔ Row 25.: 2025_PHED_885259_1 extracted
✔ Row 26.

TimeoutException: Message: 
Stacktrace:
	GetHandleVerifier [0x0x7ff618346b55+79621]
	GetHandleVerifier [0x0x7ff618346bb0+79712]
	(No symbol) [0x0x7ff6180dc0ea]
	(No symbol) [0x0x7ff618132f56]
	(No symbol) [0x0x7ff61813320c]
	(No symbol) [0x0x7ff6181865b7]
	(No symbol) [0x0x7ff61815b17f]
	(No symbol) [0x0x7ff6181833d0]
	(No symbol) [0x0x7ff61815af13]
	(No symbol) [0x0x7ff618124151]
	(No symbol) [0x0x7ff618124ee3]
	GetHandleVerifier [0x0x7ff61860686d+2962461]
	GetHandleVerifier [0x0x7ff618600b8d+2938685]
	GetHandleVerifier [0x0x7ff61861f74d+3064573]
	GetHandleVerifier [0x0x7ff618360c9e+186446]
	GetHandleVerifier [0x0x7ff618368a6f+218655]
	GetHandleVerifier [0x0x7ff61834f944+115956]
	GetHandleVerifier [0x0x7ff61834faf9+116393]
	GetHandleVerifier [0x0x7ff618335f28+10968]
	BaseThreadInitThunk [0x0x7ffaea1cdbe7+23]
	RtlUserThreadStart [0x0x7ffaeb485a4c+44]


In [2]:
import pandas as pd

# Assuming 'all_data' is your scraped list of dictionaries
df = pd.DataFrame(all_data)

# Save directly to Excel
output_file = "WB_PAST_PHE.xlsx"
df.to_excel(output_file, index=False)

print(f"✅ Saved {len(df)} records to {output_file}")


✅ Saved 5828 records to WB_PAST_PHE.xlsx


In [5]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait, Select
from selenium.webdriver.support import expected_conditions as EC
import pandas as pd
import time, os

# ─── CONFIG ─────────────────────────────────────────────────────────────
URL               = "https://wbtenders.gov.in/nicgep/app?page=WebTenderStatusLists&service=page"
DEPARTMENT_VALUE  = "292"   # ← set this to the Assam-specific value
DEPARTMENT_NAME   = "WBSIDCL"      # will be populated at runtime
FROM_DATE         = "01/07/2024"
TO_DATE           = "31/07/2025"
OUTPUT_XLS        = "WB_PAST_WBSIDCL.xlsx"

# ─── BROWSER SETUP ──────────────────────────────────────────────────────
driver = webdriver.Chrome()
driver.maximize_window()
driver.get(URL)
time.sleep(2)

# ─── PICK DEPARTMENT ────────────────────────────────────────────────────
select = Select(driver.find_element(By.ID, "OrganName"))
select.select_by_value(DEPARTMENT_VALUE)
DEPARTMENT_NAME = select.first_selected_option.text.strip()
print(f"🔎 Using Department: {DEPARTMENT_NAME}")

# ─── SET DATE FILTERS ───────────────────────────────────────────────────
for fld_id, val in [("publishedFromDate", FROM_DATE), ("publishedToDate", TO_DATE)]:
    el = driver.find_element(By.ID, fld_id)
    driver.execute_script("arguments[0].removeAttribute('readonly')", el)
    el.clear()
    el.send_keys(val)

# ─── CAPTCHA ───────────────────────────────────────────────────────────
png = "captcha_WB.png"
with open(png, "wb") as f:
    f.write(driver.find_element(By.ID, "captchaImage").screenshot_as_png)
print(f"✔ CAPTCHA saved to {png}. Please open it to read.")
captcha = input("Enter CAPTCHA: ")
driver.find_element(By.ID, "captchaText").send_keys(captcha)
driver.find_element(By.ID, "Search").click()
WebDriverWait(driver, 20).until(EC.presence_of_element_located((By.ID, "tabList")))

# ─── FIELD EXTRACTOR ────────────────────────────────────────────────────
def get_field_value(label):
    target = label.strip().lower()
    captions = driver.find_elements(By.XPATH, "//td[contains(@class,'caption')]")
    for cap in captions:
        if target in cap.text.strip().lower():
            try:
                return cap.find_element(By.XPATH, "following-sibling::td[1]").text.strip()
            except:
                return ""
    return ""

# ─── SCRAPE & PAGINATE ──────────────────────────────────────────────────
all_data = []

while True:
    rows = driver.find_elements(By.XPATH, "//table[@id='tabList']//tr[@class='even' or @class='odd']")
    for idx in range(len(rows)):
        try:
            # refresh row list each iteration
            rows = driver.find_elements(By.XPATH, "//table[@id='tabList']//tr[@class='even' or @class='odd']")
            row = rows[idx]
            cells = row.find_elements(By.TAG_NAME, "td")
            if len(cells) < 6:
                continue

            sno, tid, title, orgs, stage, status = [c.text.strip() for c in cells[:6]]

            # open detail popup
            row.find_element(By.XPATH, ".//td[last()]/a").click()
            WebDriverWait(driver, 10).until(EC.element_to_be_clickable((By.ID, "DirectLink"))).click()
            WebDriverWait(driver, 10).until(lambda d: len(d.window_handles) > 1)
            driver.switch_to.window(driver.window_handles[-1])
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.TAG_NAME, "table")))

            # extract fields
            record = {
                "Department":               DEPARTMENT_NAME,
                "S.No":                     sno.rstrip('.'),
                "Tender ID":                tid,
                "Title & Ref No.":          title,
                "Organisation Chain":       orgs,
                "Tender Stage":             stage,
                "Status":                   status,
                "Publish Date":             get_field_value("Publish Date"),
                "Bid Submission End":       get_field_value("Bid Submission End Date"),
                "Tender Value (₹)":         get_field_value("Tender Value"),
                "Location":                 get_field_value("Location"),
                "Pincode":                  get_field_value("Pincode"),
                "Period Of Work (Days)":    get_field_value("Period Of Work"),
                "Address":                  get_field_value("Address"),
            }
            all_data.append(record)
            print(f"✔ Row {sno}: {tid} extracted")

            # close detail and return to list
            driver.close()
            driver.switch_to.window(driver.window_handles[0])
            WebDriverWait(driver, 10).until(
                EC.element_to_be_clickable((By.XPATH, "//a[contains(text(),'Back')]"))
            ).click()
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.ID, "tabList")))

        except Exception as e:
            print(f"❌ Row {idx+1} error: {e}")
            driver.switch_to.window(driver.window_handles[0])
            WebDriverWait(driver, 10).until(EC.presence_of_element_located((By.ID, "tabList")))

    # move to next page, if any
    try:
        driver.find_element(By.ID, "loadNext").click()
        WebDriverWait(driver, 20).until(EC.presence_of_element_located((By.ID, "tabList")))
    except:
        break

# ─── EXPORT TO EXCEL ───────────────────────────────────────────────────
df = pd.DataFrame(all_data)
df.to_excel(OUTPUT_XLS, index=False)
print(f"\n✅ Done! Saved {len(all_data)} records to {OUTPUT_XLS}")

driver.quit()


🔎 Using Department: WBSIDCL
✔ CAPTCHA saved to captcha_WB.png. Please open it to read.


Enter CAPTCHA:  KseBcP


✔ Row 1.: 2025_MSMET_885778_1 extracted
✔ Row 2.: 2025_MSMET_885753_1 extracted
✔ Row 3.: 2025_MSMET_885703_1 extracted
✔ Row 4.: 2025_MSMET_885685_1 extracted
✔ Row 5.: 2025_MSMET_885672_1 extracted
✔ Row 6.: 2025_MSMET_885261_1 extracted
✔ Row 7.: 2025_MSMET_885233_1 extracted
✔ Row 8.: 2025_MSMET_885137_1 extracted
✔ Row 9.: 2025_MSMET_885131_1 extracted
✔ Row 10.: 2025_MSMET_885120_1 extracted
✔ Row 11.: 2025_MSMET_884986_1 extracted
✔ Row 12.: 2025_MSMET_884975_1 extracted
✔ Row 13.: 2025_MSMET_884733_1 extracted
✔ Row 14.: 2025_MSMET_884107_1 extracted
✔ Row 15.: 2025_MSMET_883968_1 extracted
✔ Row 16.: 2025_MSMET_883557_1 extracted
✔ Row 17.: 2025_MSMET_883527_1 extracted
✔ Row 18.: 2025_MSMET_882934_1 extracted
✔ Row 19.: 2025_MSMET_882923_1 extracted
✔ Row 20.: 2025_MSMET_882912_1 extracted
✔ Row 21.: 2025_MSMET_882897_1 extracted
✔ Row 22.: 2025_MSMET_882705_1 extracted
✔ Row 23.: 2025_MSMET_882630_1 extracted
✔ Row 24.: 2025_MSMET_882619_1 extracted
✔ Row 25.: 2025_MSMET_882

In [3]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.ui import WebDriverWait, Select
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import (
    TimeoutException, NoSuchElementException, StaleElementReferenceException,
)
from datetime import datetime
import pandas as pd, os, re, shutil, time

# ───────────────── CONFIG ─────────────────
URL = ("https://wbtenders.gov.in/nicgep/app?page=WebTenderStatusLists&service=page")
DEPTS = [("PHE","209")]

published_from = "01/07/2024"  # dd/MM/yyyy format
published_to = "31/07/2025"

# Clean department name to avoid spaces in filename
dept_name_clean = DEPTS[0][0].replace(" ", "_")
OUT_XLSX = f"WB_tenders_{dept_name_clean}_{datetime.today().strftime('%d_%m_%Y')}.xlsx"

DL_ROOT = os.path.join(os.getcwd(), "downloads")
os.makedirs(DL_ROOT, exist_ok=True)
_clean = lambda s: re.sub(r"[^\d.]", "", s.strip())

def dept_dir(name: str) -> str:
    p = os.path.join(DL_ROOT, name)
    os.makedirs(p, exist_ok=True)
    return p

def await_download(before, target_dir, timeout=40):
    WebDriverWait(drv, timeout).until(
        lambda _: any(f.endswith((".xls", ".xlsx", ".pdf")) and not f.endswith(".crdownload")
                      for f in set(os.listdir(DL_ROOT)) - before))
    f = next(x for x in os.listdir(DL_ROOT) if x not in before and not x.endswith(".crdownload"))
    shutil.move(os.path.join(DL_ROOT, f), os.path.join(target_dir, f))
    print(f"⬇️  Downloaded file: {f} → {target_dir}")

# ───────────── DRIVER ─────────────
opt = webdriver.ChromeOptions()
opt.add_experimental_option("prefs", {
    "download.default_directory": DL_ROOT,
    "download.prompt_for_download": False,
    "safebrowsing.enabled": True
})
drv = webdriver.Chrome(options=opt)
drv.maximize_window()
print(f"📅  {published_from} → {published_to}")

all_rows = []
try:
    drv.get(URL)
    time.sleep(2)

    # Manual CAPTCHA - save image and prompt user input
    open("captcha.png", "wb").write(
        drv.find_element(By.ID, "captchaImage").screenshot_as_png)
    try:
        os.startfile("captcha.png")  # Windows only; adjust for others
    except FileNotFoundError:
        pass
    drv.find_element(By.ID, "captchaText").send_keys(input("Enter CAPTCHA: "))
    print("✅ CAPTCHA solved.\n")

    main_tab = drv.current_window_handle

    # ───────────── MAIN LOOP ─────────────
    for dept, val in DEPTS:
        print(f"🔍 {dept}")
        Select(drv.find_element(By.ID, "OrganName")).select_by_value(val)

        for box, date in [("publishedFromDate", published_from),
                          ("publishedToDate", published_to)]:
            drv.execute_script(
                "document.getElementById(arguments[0]).removeAttribute('readonly');", box)
            elm = drv.find_element(By.ID, box)
            elm.clear()
            elm.send_keys(date)

        drv.find_element(By.ID, "Search").click()
        WebDriverWait(drv, 30).until(
            EC.presence_of_element_located((By.ID, "tabList")))

        page = 1
        while True:
            rows = drv.find_elements(By.XPATH, "//table[@id='tabList']//tr[td]")
            if len(rows) == 1 and "No Data" in rows[0].text:
                break

            for row in rows:
                try:
                    tds = row.find_elements(By.TAG_NAME, "td")
                    if len(tds) < 6:
                        continue
                    anchors = tds[5].find_elements(By.TAG_NAME, "a")
                    if not anchors:
                        continue  # skip heading rows

                    sno, tid = [tds[i].text.strip() for i in (0, 1)]

                    # open status in new tab
                    link = anchors[0]
                    drv.execute_script("arguments[0].setAttribute('target','_blank');", link)
                    link.send_keys(Keys.CONTROL + Keys.RETURN)
                    WebDriverWait(drv, 8).until(
                        lambda d: len(d.window_handles) > 1)
                    detail_tab = [h for h in drv.window_handles if h != main_tab][-1]
                    drv.switch_to.window(detail_tab)

                    # View More Details
                    WebDriverWait(drv, 8).until(
                        EC.element_to_be_clickable(
                            (By.XPATH, "//a[contains(text(),'View More Details')]"))
                    ).click()

                    # BOQ
                    remark = "No"
                    save_to = os.path.join(dept_dir(dept), tid)
                    os.makedirs(save_to, exist_ok=True)

                    try:
                        # direct link on detail
                        direct = drv.find_elements(
                            By.XPATH,
                            "//a[@id='BOQ' or contains(text(),'BOQ Comparative Chart') or "
                            "contains(@href,'FrontEndViewBidSummaryDetailsPrint')]")
                        if direct:
                            before = set(os.listdir(DL_ROOT))
                            direct[0].click()
                            await_download(before, save_to)
                            remark = "Yes"
                        else:
                            # stage summary pop-up
                            stage_link = WebDriverWait(drv, 6).until(
                                EC.element_to_be_clickable((
                                    By.XPATH, "//a[contains(@onclick,'openPopUp') or "
                                              "starts-with(@id,'DirectLink_')]")))
                            stage_link.send_keys(Keys.CONTROL + Keys.RETURN)
                            WebDriverWait(drv, 6).until(
                                lambda d: len(d.window_handles) > 2)
                            pop = [h for h in drv.window_handles
                                   if h not in (main_tab, detail_tab)][0]
                            drv.switch_to.window(pop)
                            chart = WebDriverWait(drv, 8).until(
                                EC.element_to_be_clickable(
                                    (By.XPATH, "//*[@id='BOQ' or starts-with(@id,'CHART')]")))
                            before = set(os.listdir(DL_ROOT))
                            chart.click()
                            await_download(before, save_to)
                            remark = "Yes"
                    except Exception:
                        pass

                    # close extra tabs
                    for h in [h for h in drv.window_handles if h != main_tab]:
                        drv.switch_to.window(h)
                        drv.close()
                    drv.switch_to.window(main_tab)

                    all_rows.append({
                        "Department": dept,
                        "S.No": sno,
                        "Tender ID": tid,
                        "Remark": remark
                    })
                    print(f"   ➕ {tid} ({remark})")
                except (StaleElementReferenceException, NoSuchElementException) as e:
                    print(f"⚠️ Skipping a row due to: {e}")
                    continue
                except Exception as e:
                    print(f"⚠️ Error processing tender {tid}: {e}")
                    continue

            print(f"📃 Collected so far: {len(all_rows)} | page {page}")
            page += 1

            # next page
            try:
                drv.find_element(By.ID, "loadNext").click()
                WebDriverWait(drv, 8).until(
                    EC.presence_of_element_located((By.ID, "tabList")))
            except Exception:
                break

finally:
    if all_rows:
        pd.DataFrame(all_rows).to_excel(OUT_XLSX, index=False)
        print(f"\n✅ Rows written: {len(all_rows)} → {OUT_XLSX}")
        print(f"📂 BOQs → {DL_ROOT}/<Department>/<TenderID>/")
    else:
        print("\n⚠️ Script finished but collected ZERO rows — "
              "verify the date filter or that tenders exist.")
    drv.quit()


📅  01/07/2024 → 31/07/2025


Enter CAPTCHA:  2t7u6p


✅ CAPTCHA solved.

🔍 PHE
   ➕ 2025_PHED_885801_5 (No)
   ➕ 2025_PHED_885801_4 (No)
   ➕ 2025_PHED_885801_3 (No)
   ➕ 2025_PHED_885801_2 (No)
   ➕ 2025_PHED_885801_1 (No)
   ➕ 2025_PHED_885780_2 (No)
   ➕ 2025_PHED_885780_1 (No)
   ➕ 2025_PHED_885621_2 (No)
   ➕ 2025_PHED_885621_1 (No)
   ➕ 2025_PHED_885613_1 (No)
📃 Collected so far: 10 | page 1
   ➕ 2025_PHED_889617_2 (No)
   ➕ 2025_PHED_889617_1 (No)
   ➕ 2025_PHED_889552_9 (No)
   ➕ 2025_PHED_889552_8 (No)
   ➕ 2025_PHED_889552_7 (No)
   ➕ 2025_PHED_889552_6 (No)
   ➕ 2025_PHED_889552_5 (No)
   ➕ 2025_PHED_889552_4 (No)
   ➕ 2025_PHED_889552_3 (No)
   ➕ 2025_PHED_889552_27 (No)
📃 Collected so far: 20 | page 2
   ➕ 2025_PHED_889552_26 (No)
   ➕ 2025_PHED_889552_25 (No)
   ➕ 2025_PHED_889552_24 (No)
   ➕ 2025_PHED_889552_23 (No)
   ➕ 2025_PHED_889552_22 (No)
   ➕ 2025_PHED_889552_21 (No)
   ➕ 2025_PHED_889552_20 (No)
   ➕ 2025_PHED_889552_2 (No)
   ➕ 2025_PHED_889552_19 (No)
   ➕ 2025_PHED_889552_18 (No)
📃 Collected so far: 30 | page 3

In [3]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.ui import WebDriverWait, Select
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import (
    TimeoutException, NoSuchElementException, StaleElementReferenceException,
)
from datetime import datetime
import pandas as pd, os, re, shutil, time

# ───────────────── CONFIG ─────────────────
URL = ("https://tripuratenders.gov.in/nicgep/app?page=WebTenderStatusLists&service=page")
DEPTS = [("Tripura Urban Planning and Development Authority(ADB Tender)","156")]

published_from = "01/07/2024"  # dd/MM/yyyy format
published_to = "31/07/2025"

# Clean department name to avoid spaces in filename
dept_name_clean = DEPTS[0][0].replace(" ", "_")
OUT_XLSX = f"Tripura_tenders_{dept_name_clean}_{datetime.today().strftime('%d_%m_%Y')}.xlsx"

DL_ROOT = os.path.join(os.getcwd(), "downloads")
os.makedirs(DL_ROOT, exist_ok=True)
_clean = lambda s: re.sub(r"[^\d.]", "", s.strip())

def dept_dir(name: str) -> str:
    p = os.path.join(DL_ROOT, name)
    os.makedirs(p, exist_ok=True)
    return p

def await_download(before, target_dir, timeout=40):
    WebDriverWait(drv, timeout).until(
        lambda _: any(f.endswith((".xls", ".xlsx", ".pdf")) and not f.endswith(".crdownload")
                      for f in set(os.listdir(DL_ROOT)) - before))
    f = next(x for x in os.listdir(DL_ROOT) if x not in before and not x.endswith(".crdownload"))
    shutil.move(os.path.join(DL_ROOT, f), os.path.join(target_dir, f))
    print(f"⬇️  Downloaded file: {f} → {target_dir}")

# ───────────── DRIVER ─────────────
opt = webdriver.ChromeOptions()
opt.add_experimental_option("prefs", {
    "download.default_directory": DL_ROOT,
    "download.prompt_for_download": False,
    "safebrowsing.enabled": True
})
drv = webdriver.Chrome(options=opt)
drv.maximize_window()
print(f"📅  {published_from} → {published_to}")

all_rows = []
try:
    drv.get(URL)
    time.sleep(2)

    # Manual CAPTCHA - save image and prompt user input
    open("captcha.png", "wb").write(
        drv.find_element(By.ID, "captchaImage").screenshot_as_png)
    try:
        os.startfile("captcha.png")  # Windows only; adjust for others
    except FileNotFoundError:
        pass
    drv.find_element(By.ID, "captchaText").send_keys(input("Enter CAPTCHA: "))
    print("✅ CAPTCHA solved.\n")

    main_tab = drv.current_window_handle

    # ───────────── MAIN LOOP ─────────────
    for dept, val in DEPTS:
        print(f"🔍 {dept}")
        Select(drv.find_element(By.ID, "OrganName")).select_by_value(val)

        for box, date in [("publishedFromDate", published_from),
                          ("publishedToDate", published_to)]:
            drv.execute_script(
                "document.getElementById(arguments[0]).removeAttribute('readonly');", box)
            elm = drv.find_element(By.ID, box)
            elm.clear()
            elm.send_keys(date)

        drv.find_element(By.ID, "Search").click()
        WebDriverWait(drv, 30).until(
            EC.presence_of_element_located((By.ID, "tabList")))

        page = 1
        while True:
            rows = drv.find_elements(By.XPATH, "//table[@id='tabList']//tr[td]")
            if len(rows) == 1 and "No Data" in rows[0].text:
                break

            for row in rows:
                try:
                    tds = row.find_elements(By.TAG_NAME, "td")
                    if len(tds) < 6:
                        continue
                    anchors = tds[5].find_elements(By.TAG_NAME, "a")
                    if not anchors:
                        continue  # skip heading rows

                    sno, tid = [tds[i].text.strip() for i in (0, 1)]

                    # open status in new tab
                    link = anchors[0]
                    drv.execute_script("arguments[0].setAttribute('target','_blank');", link)
                    link.send_keys(Keys.CONTROL + Keys.RETURN)
                    WebDriverWait(drv, 8).until(
                        lambda d: len(d.window_handles) > 1)
                    detail_tab = [h for h in drv.window_handles if h != main_tab][-1]
                    drv.switch_to.window(detail_tab)

                    # View More Details
                    WebDriverWait(drv, 8).until(
                        EC.element_to_be_clickable(
                            (By.XPATH, "//a[contains(text(),'View More Details')]"))
                    ).click()

                    # BOQ
                    remark = "No"
                    save_to = os.path.join(dept_dir(dept), tid)
                    os.makedirs(save_to, exist_ok=True)

                    try:
                        # direct link on detail
                        direct = drv.find_elements(
                            By.XPATH,
                            "//a[@id='BOQ' or contains(text(),'BOQ Comparative Chart') or "
                            "contains(@href,'FrontEndViewBidSummaryDetailsPrint')]")
                        if direct:
                            before = set(os.listdir(DL_ROOT))
                            direct[0].click()
                            await_download(before, save_to)
                            remark = "Yes"
                        else:
                            # stage summary pop-up
                            stage_link = WebDriverWait(drv, 6).until(
                                EC.element_to_be_clickable((
                                    By.XPATH, "//a[contains(@onclick,'openPopUp') or "
                                              "starts-with(@id,'DirectLink_')]")))
                            stage_link.send_keys(Keys.CONTROL + Keys.RETURN)
                            WebDriverWait(drv, 6).until(
                                lambda d: len(d.window_handles) > 2)
                            pop = [h for h in drv.window_handles
                                   if h not in (main_tab, detail_tab)][0]
                            drv.switch_to.window(pop)
                            chart = WebDriverWait(drv, 8).until(
                                EC.element_to_be_clickable(
                                    (By.XPATH, "//*[@id='BOQ' or starts-with(@id,'CHART')]")))
                            before = set(os.listdir(DL_ROOT))
                            chart.click()
                            await_download(before, save_to)
                            remark = "Yes"
                    except Exception:
                        pass

                    # close extra tabs
                    for h in [h for h in drv.window_handles if h != main_tab]:
                        drv.switch_to.window(h)
                        drv.close()
                    drv.switch_to.window(main_tab)

                    all_rows.append({
                        "Department": dept,
                        "S.No": sno,
                        "Tender ID": tid,
                        "Remark": remark
                    })
                    print(f"   ➕ {tid} ({remark})")
                except (StaleElementReferenceException, NoSuchElementException) as e:
                    print(f"⚠️ Skipping a row due to: {e}")
                    continue
                except Exception as e:
                    print(f"⚠️ Error processing tender {tid}: {e}")
                    continue

            print(f"📃 Collected so far: {len(all_rows)} | page {page}")
            page += 1

            # next page
            try:
                drv.find_element(By.ID, "loadNext").click()
                WebDriverWait(drv, 8).until(
                    EC.presence_of_element_located((By.ID, "tabList")))
            except Exception:
                break

finally:
    if all_rows:
        pd.DataFrame(all_rows).to_excel(OUT_XLSX, index=False)
        print(f"\n✅ Rows written: {len(all_rows)} → {OUT_XLSX}")
        print(f"📂 BOQs → {DL_ROOT}/<Department>/<TenderID>/")
    else:
        print("\n⚠️ Script finished but collected ZERO rows — "
              "verify the date filter or that tenders exist.")
    drv.quit()


📅  01/07/2024 → 31/07/2025


Enter CAPTCHA:  At8pvd


✅ CAPTCHA solved.

🔍 Tripura Urban Planning and Development Authority(ADB Tender)
⬇️  Downloaded file: boqcomparativechart (1).xlsx → C:\Users\Jaydeb\downloads\Tripura Urban Planning and Development Authority(ADB Tender)\2024_TUDAW_53697_2
   ➕ 2024_TUDAW_53697_2 (Yes)
   ➕ 2024_TUDAW_53697_1 (No)
⬇️  Downloaded file: boqcomparativechart (1).xlsx → C:\Users\Jaydeb\downloads\Tripura Urban Planning and Development Authority(ADB Tender)\2024_TUDAW_51700_1
   ➕ 2024_TUDAW_51700_1 (Yes)
📃 Collected so far: 3 | page 1

✅ Rows written: 3 → Tripura_tenders_Tripura_Urban_Planning_and_Development_Authority(ADB_Tender)_18_08_2025.xlsx
📂 BOQs → C:\Users\Jaydeb\downloads/<Department>/<TenderID>/


In [10]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.ui import WebDriverWait, Select
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import (
    TimeoutException, NoSuchElementException, StaleElementReferenceException,
)
from datetime import datetime
import pandas as pd, os, re, shutil, time

# ───────────────── CONFIG ─────────────────
URL = ("https://manipurtenders.gov.in/nicgep/app?page=WebTenderStatusLists&service=page")
DEPTS = [("Rural Development and Panchayati Raj","60")]

published_from = "01/07/2024"  # dd/MM/yyyy format
published_to = "31/07/2025"

# Clean department name to avoid spaces in filename
dept_name_clean = DEPTS[0][0].replace(" ", "_")
OUT_XLSX = f"Manipur_tenders_{dept_name_clean}_{datetime.today().strftime('%d_%m_%Y')}.xlsx"

DL_ROOT = os.path.join(os.getcwd(), "downloads")
os.makedirs(DL_ROOT, exist_ok=True)
_clean = lambda s: re.sub(r"[^\d.]", "", s.strip())

def dept_dir(name: str) -> str:
    p = os.path.join(DL_ROOT, name)
    os.makedirs(p, exist_ok=True)
    return p

def await_download(before, target_dir, timeout=40):
    WebDriverWait(drv, timeout).until(
        lambda _: any(f.endswith((".xls", ".xlsx", ".pdf")) and not f.endswith(".crdownload")
                      for f in set(os.listdir(DL_ROOT)) - before))
    f = next(x for x in os.listdir(DL_ROOT) if x not in before and not x.endswith(".crdownload"))
    shutil.move(os.path.join(DL_ROOT, f), os.path.join(target_dir, f))
    print(f"⬇️  Downloaded file: {f} → {target_dir}")

# ───────────── DRIVER ─────────────
opt = webdriver.ChromeOptions()
opt.add_experimental_option("prefs", {
    "download.default_directory": DL_ROOT,
    "download.prompt_for_download": False,
    "safebrowsing.enabled": True
})
drv = webdriver.Chrome(options=opt)
drv.maximize_window()
print(f"📅  {published_from} → {published_to}")

all_rows = []
try:
    drv.get(URL)
    time.sleep(2)

    # Manual CAPTCHA - save image and prompt user input
    open("captcha.png", "wb").write(
        drv.find_element(By.ID, "captchaImage").screenshot_as_png)
    try:
        os.startfile("captcha.png")  # Windows only; adjust for others
    except FileNotFoundError:
        pass
    drv.find_element(By.ID, "captchaText").send_keys(input("Enter CAPTCHA: "))
    print("✅ CAPTCHA solved.\n")

    main_tab = drv.current_window_handle

    # ───────────── MAIN LOOP ─────────────
    for dept, val in DEPTS:
        print(f"🔍 {dept}")
        Select(drv.find_element(By.ID, "OrganName")).select_by_value(val)

        for box, date in [("publishedFromDate", published_from),
                          ("publishedToDate", published_to)]:
            drv.execute_script(
                "document.getElementById(arguments[0]).removeAttribute('readonly');", box)
            elm = drv.find_element(By.ID, box)
            elm.clear()
            elm.send_keys(date)

        drv.find_element(By.ID, "Search").click()
        WebDriverWait(drv, 30).until(
            EC.presence_of_element_located((By.ID, "tabList")))

        page = 1
        while True:
            rows = drv.find_elements(By.XPATH, "//table[@id='tabList']//tr[td]")
            if len(rows) == 1 and "No Data" in rows[0].text:
                break

            for row in rows:
                try:
                    tds = row.find_elements(By.TAG_NAME, "td")
                    if len(tds) < 6:
                        continue
                    anchors = tds[5].find_elements(By.TAG_NAME, "a")
                    if not anchors:
                        continue  # skip heading rows

                    sno, tid = [tds[i].text.strip() for i in (0, 1)]

                    # open status in new tab
                    link = anchors[0]
                    drv.execute_script("arguments[0].setAttribute('target','_blank');", link)
                    link.send_keys(Keys.CONTROL + Keys.RETURN)
                    WebDriverWait(drv, 8).until(
                        lambda d: len(d.window_handles) > 1)
                    detail_tab = [h for h in drv.window_handles if h != main_tab][-1]
                    drv.switch_to.window(detail_tab)

                    # View More Details
                    WebDriverWait(drv, 8).until(
                        EC.element_to_be_clickable(
                            (By.XPATH, "//a[contains(text(),'View More Details')]"))
                    ).click()

                    # BOQ
                    remark = "No"
                    save_to = os.path.join(dept_dir(dept), tid)
                    os.makedirs(save_to, exist_ok=True)

                    try:
                        # direct link on detail
                        direct = drv.find_elements(
                            By.XPATH,
                            "//a[@id='BOQ' or contains(text(),'BOQ Comparative Chart') or "
                            "contains(@href,'FrontEndViewBidSummaryDetailsPrint')]")
                        if direct:
                            before = set(os.listdir(DL_ROOT))
                            direct[0].click()
                            await_download(before, save_to)
                            remark = "Yes"
                        else:
                            # stage summary pop-up
                            stage_link = WebDriverWait(drv, 6).until(
                                EC.element_to_be_clickable((
                                    By.XPATH, "//a[contains(@onclick,'openPopUp') or "
                                              "starts-with(@id,'DirectLink_')]")))
                            stage_link.send_keys(Keys.CONTROL + Keys.RETURN)
                            WebDriverWait(drv, 6).until(
                                lambda d: len(d.window_handles) > 2)
                            pop = [h for h in drv.window_handles
                                   if h not in (main_tab, detail_tab)][0]
                            drv.switch_to.window(pop)
                            chart = WebDriverWait(drv, 8).until(
                                EC.element_to_be_clickable(
                                    (By.XPATH, "//*[@id='BOQ' or starts-with(@id,'CHART')]")))
                            before = set(os.listdir(DL_ROOT))
                            chart.click()
                            await_download(before, save_to)
                            remark = "Yes"
                    except Exception:
                        pass

                    # close extra tabs
                    for h in [h for h in drv.window_handles if h != main_tab]:
                        drv.switch_to.window(h)
                        drv.close()
                    drv.switch_to.window(main_tab)

                    all_rows.append({
                        "Department": dept,
                        "S.No": sno,
                        "Tender ID": tid,
                        "Remark": remark
                    })
                    print(f"   ➕ {tid} ({remark})")
                except (StaleElementReferenceException, NoSuchElementException) as e:
                    print(f"⚠️ Skipping a row due to: {e}")
                    continue
                except Exception as e:
                    print(f"⚠️ Error processing tender {tid}: {e}")
                    continue

            print(f"📃 Collected so far: {len(all_rows)} | page {page}")
            page += 1

            # next page
            try:
                drv.find_element(By.ID, "loadNext").click()
                WebDriverWait(drv, 8).until(
                    EC.presence_of_element_located((By.ID, "tabList")))
            except Exception:
                break

finally:
    if all_rows:
        pd.DataFrame(all_rows).to_excel(OUT_XLSX, index=False)
        print(f"\n✅ Rows written: {len(all_rows)} → {OUT_XLSX}")
        print(f"📂 BOQs → {DL_ROOT}/<Department>/<TenderID>/")
    else:
        print("\n⚠️ Script finished but collected ZERO rows — "
              "verify the date filter or that tenders exist.")
    drv.quit()


📅  01/07/2024 → 31/07/2025


Enter CAPTCHA:  2ykcuu


✅ CAPTCHA solved.

🔍 Rural Development and Panchayati Raj
   ➕ 2025_RDnPR_2878_1 (No)
⬇️  Downloaded file: boqcomparativechart (1).xlsx → C:\Users\Jaydeb\downloads\Rural Development and Panchayati Raj\2025_RDnPR_2869_1
   ➕ 2025_RDnPR_2869_1 (Yes)
⬇️  Downloaded file: boqcomparativechart (1).xlsx → C:\Users\Jaydeb\downloads\Rural Development and Panchayati Raj\2025_RDnPR_2824_4
   ➕ 2025_RDnPR_2824_4 (Yes)
⬇️  Downloaded file: boqcomparativechart (1).xlsx → C:\Users\Jaydeb\downloads\Rural Development and Panchayati Raj\2025_RDnPR_2824_3
   ➕ 2025_RDnPR_2824_3 (Yes)
⬇️  Downloaded file: boqcomparativechart (1).xlsx → C:\Users\Jaydeb\downloads\Rural Development and Panchayati Raj\2025_RDnPR_2824_2
   ➕ 2025_RDnPR_2824_2 (Yes)
⬇️  Downloaded file: boqcomparativechart (1).xlsx → C:\Users\Jaydeb\downloads\Rural Development and Panchayati Raj\2025_RDnPR_2824_1
   ➕ 2025_RDnPR_2824_1 (Yes)
⬇️  Downloaded file: boqcomparativechart (1).xlsx → C:\Users\Jaydeb\downloads\Rural Development and Panc